Question 1 Find all players who represent India. Display their full name, playing role, batting style, and bowling style.

In [ ]:
import requests
url = "https://cricbuzz-cricket.p.rapidapi.com/teams/v1/2/players" #GET - teams/get-players

headers = {
	"x-rapidapi-key": "316be0a36dmsh4662afd995a02bbp1c7c24jsn649cce21a961",
	"x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}

response = requests.get(url, headers=headers)
data = response.json()
print(data)

In [ ]:
import requests
import psycopg2 as db
conn = db.connect(host="localhost", port="5432", dbname="Cricbuzz", user="postgres", password="Tanvikha@1998")
print("connected to DB")

cursor = conn.cursor()

players = []
count=0
for p in data.get("player"):
    name = p.get("name")
    batting = p.get("battingStyle")
    bowling = p.get("bowlingStyle")
    player_id = p.get("id")
    print(player_id)
    url = "https://cricbuzz-cricket.p.rapidapi.com/stats/v1/player/{player_id}" #GET - players/get-info
    headers = {
	"x-rapidapi-key": "316be0a36dmsh4662afd995a02bbp1c7c24jsn649cce21a961",
	"x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
   }
    response = requests.get(url, headers=headers)
    data2 = response.json()
    role = data2.get("role")
    print(data2)

In [ ]:
import requests
import psycopg2 as db

conn = db.connect(
    host="localhost",
    port="5432",
    dbname="Cricbuzz",
    user="postgres",
    password="Tanvikha@1998"
)
print("Connected to DB")

cursor = conn.cursor()

players = []
count = 0

for p in data.get("player", []):
    name = p.get("name")
    batting = p.get("battingStyle")
    bowling = p.get("bowlingStyle")
    player_id = p.get("id")

    url = f"https://cricbuzz-cricket.p.rapidapi.com/stats/v1/player/{player_id}"

    headers = {
        "x-rapidapi-key": "fd6e4d07ecmsh49365d41af0234bp1150e6jsna57cb2598212",
        "x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
    }

    response = requests.get(url, headers=headers)

    if response.status_code != 200:
        print(f"Failed to fetch data for player {name} ({player_id}): {response.status_code}")
        continue

    data2 = response.json()
    role = data2.get("role")

    players.append({
        "Id": player_id,
        "Name": name,
        "BattingStyle": batting,
        "BowlingStyle": bowling,
        "Role": role
    })

    try:
        cursor.execute(
            """
            INSERT INTO indianPlayers_1 (PlayerId, PlayerName, BattingStyle, BowlingStyle, PlayingRole)
            VALUES (%s, %s, %s, %s, %s)
            ON CONFLICT (PlayerId) DO NOTHING
            """,
            (player_id, name, batting, bowling, role)
        )
        count += 1

    except Exception as e:
        print(f" Error inserting player {name}: {e}")

conn.commit()
print(f" Done inserting {count} players")
conn.close()


In [ ]:
import psycopg2 as db
conn = db.connect(host="localhost", port="5432", dbname="Cricbuzz", user="postgres", password="Tanvikha@1998")
print("connected to DB")

cur = conn.cursor()
cur.execute("""create table if not exists indianPlayers_1(PlayerId int,PlayerName varchar(20), BattingStyle varchar(20), 
            BowlingStyle varchar(20),PlayingRole varchar(20))""")

conn.commit()
cur.close()
conn.close()

In [ ]:
import requests
import psycopg2 as db

conn = db.connect(
    host="localhost",
    port="5432",
    dbname="Cricbuzz",
    user="postgres",
    password="Tanvikha@1998"
)
print(" Connected to DB")

cursor = conn.cursor()


url_players = "https://cricbuzz-cricket.p.rapidapi.com/teams/v1/2/players"  # 2 = India
headers = {
	"x-rapidapi-key": "316be0a36dmsh4662afd995a02bbp1c7c24jsn649cce21a961",
	"x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}

response = requests.get(url_players, headers=headers)
if response.status_code != 200:
    raise Exception(f" Failed to get players list: {response.status_code}")

data = response.json()


players = []
count = 0

for p in data.get("player", []):
    name = p.get("name")
    batting = p.get("battingStyle")
    bowling = p.get("bowlingStyle")
    player_id = p.get("id")

    print(f" Fetching details for: {name} ({player_id})")


    url = f"https://cricbuzz-cricket.p.rapidapi.com/stats/v1/player/{player_id}"
    headers = {
	"x-rapidapi-key": "316be0a36dmsh4662afd995a02bbp1c7c24jsn649cce21a961",
	"x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
    }
    response2 = requests.get(url, headers=headers)
    if response2.status_code != 200:
        print(f" Failed for {name}: {response2.status_code}")
        continue

    data2 = response2.json()
    role = data2.get("role", "Unknown")

    print(f"Name: {name}, Role: {role}, Batting: {batting}, Bowling: {bowling}")

    players.append({
        "Id": player_id,
        "Name": name,
        "BattingStyle": batting,
        "BowlingStyle": bowling,
        "Role": role
    })

    try:
        cursor.execute("""
            INSERT INTO indianPlayers_1 (PlayerId, PlayerName, BattingStyle, BowlingStyle, PlayingRole)
            VALUES (%s, %s, %s, %s, %s)""", (player_id, name, batting, bowling, role))
        conn.commit()

        print(f"Insert attempted for {name} (ID: {player_id})")
        print(cursor.query)
        count += 1

    except Exception as e:
        conn.rollback()  


conn.commit()
print(f" Done inserting {count} players.")

cursor.close()
conn.close()
print("Connection closed.")


Question 2 Show all cricket matches that were played in the last Few days. Include the match description, both team names, venue name with city, and the match date. Sort by most recent matches first.

In [3]:
import requests

url = "https://cricbuzz-cricket.p.rapidapi.com/matches/v1/recent"

headers = {
	"x-rapidapi-key": "d5744f7de2msh90e1b4c46e5734ap186e68jsncacc1ce53688",
	"x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}

response = requests.get(url, headers=headers)
data = response.json()
print(response.json())

{'typeMatches': [{'matchType': 'International', 'seriesMatches': [{'seriesAdWrapper': {'seriesId': 9638, 'seriesName': 'South Africa tour of India, 2025', 'matches': [{'matchInfo': {'matchId': 117389, 'seriesId': 9638, 'seriesName': 'South Africa tour of India, 2025', 'matchDesc': '1st ODI', 'matchFormat': 'ODI', 'startDate': '1764489600000', 'endDate': '1764518400000', 'state': 'Complete', 'status': 'India won by 17 runs', 'team1': {'teamId': 2, 'teamName': 'India', 'teamSName': 'IND', 'imageId': 776162}, 'team2': {'teamId': 11, 'teamName': 'South Africa', 'teamSName': 'RSA', 'imageId': 776287}, 'venueInfo': {'id': 291, 'ground': 'JSCA International Stadium Complex', 'city': 'Ranchi', 'timezone': '+05:30', 'latitude': '23.310158', 'longitude': '85.274824'}, 'currBatTeamId': 2, 'seriesStartDt': '1763078400000', 'seriesEndDt': '1766275200000', 'isTimeAnnounced': True, 'stateTitle': 'IND Won'}, 'matchScore': {'team1Score': {'inngs1': {'inningsId': 1, 'runs': 349, 'wickets': 8, 'overs': 4

In [16]:
from datetime import datetime
import psycopg2 as db

conn = db.connect(
    host="localhost",
    port="5432",
    dbname="Cricbuzz",
    user="postgres",
    password="Tanvikha@1998"
)
print("Connected to DB")

cursor = conn.cursor()

insert_query = """
    INSERT INTO cricket_matches_2
    (match_desc, start_date, team1, team2, ground, city, match_id)
    VALUES (%s, %s, %s, %s, %s, %s, %s)
"""

def parse_date(d):
    try:
        return datetime.strptime(d, "%Y%m%d%H%M%S")
    except:
        return None

for match in cricket_matches:
    cursor.execute(insert_query, (
        match["matchDesc"],
        parse_date(match["startDate"]),
        match["team1"],
        match["team2"],
        match["ground"],
        match["city"],
        match["matchId"]
    ))

conn.commit()
cursor.close()
conn.close()

print("Records inserted successfully!")


Connected to DB
Records inserted successfully!


In [ ]:
from datetime import datetime
import requests
import psycopg2

def parse_date(d):
    try:
        return datetime.strptime(d, "%Y%m%d%H%M%S")
    except Exception:
        return datetime.min

cricket_matches = []

for p in data.get("typeMatches", []):
    for s in p.get("seriesMatches", []):
        seriesdata = s.get("seriesAdWrapper", {})
        for m in seriesdata.get("matches", []):
            info = m.get("matchInfo", {})
            matchId = info.get("matchId")
            matchDes = info.get("matchDesc")
            startDate = info.get("startDate")

            team1 = info.get("team1", {}).get("teamName")
            team2 = info.get("team2", {}).get("teamName")

            venueInfo = info.get("venueInfo", {})
            venueId = venueInfo.get("id")

            url = f"https://cricbuzz-cricket.p.rapidapi.com/venues/v1/{venueId}"

            headers = {
                "x-rapidapi-key": "c731246330msh7b7736b1d0af948p1083c6jsn55327cfb8111",
	            "x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
            }

            try:
                response1 = requests.get(url, headers=headers, timeout=10)
                response1.raise_for_status()
                data2 = response1.json()
            except:
                data2 = {}

            ground = data2.get("ground")
            city = data2.get("city")

            cricket_matches.append({
                "matchId" : matchId,
                "matchDesc": matchDes,
                "startDate": startDate,
                "team1": team1,
                "team2": team2,
                "ground": ground,
                "city": city
            })

cricket_matches.sort(key=lambda x: parse_date(x.get("startDate", "")))

for match in cricket_matches:
    print(match)


In [ ]:
venue_ids = []
cricket_matches = [] 

for p in data.get("typeMatches", []):
    for s in p.get("seriesMatches", []):
        seriesdata = s.get("seriesAdWrapper", {})
        for m in seriesdata.get("matches", []):
            
            info = m.get("matchInfo", {})

            matchId = info.get("matchId")
            matchDes = info.get("matchDesc")
            startDate = info.get("startDate")
            team1 = info.get("team1", {}).get("teamName")
            team2 = info.get("team2", {}).get("teamName")

            venueInfo = info.get("venueInfo", {})
            venueId = venueInfo.get("id")

            if venueId:
                venue_ids.append({
                    "venueId": venueId,
                    "matchId": matchId,
                    "matchDesc": matchDes,
                    "startDate": startDate,
                    "team1": team1,
                    "team2": team2
                })

for item in venue_ids:

    venueId = item["venueId"]
    print("Fetching venue:", venueId)

    url = f"https://cricbuzz-cricket.p.rapidapi.com/venues/v1/{venueId}"

    headers = {
        "x-rapidapi-key": "c731246330msh7b7736b1d0af948p1083c6jsn55327cfb8111",
        "x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
    }

    try:
        response1 = requests.get(url, headers=headers, timeout=10)
        response1.raise_for_status()
        data2 = response1.json()
    except Exception as e:
        print("Error fetching:", venueId, e)
        data2 = {}

    ground = data2.get("ground")
    city = data2.get("city")

    cricket_matches.append({
        "matchId": item["matchId"],
        "matchDesc": item["matchDesc"],
        "startDate": item["startDate"],
        "team1": item["team1"],
        "team2": item["team2"],
        "venueId": venueId,
        "ground": ground,
        "city": city
    })

cricket_matches.sort(key=lambda x: parse_date(x.get("startDate", "")))

for match in cricket_matches:
    print(match)


In [ ]:
import requests

cricket_matches = []

for venueId in venue_ids:
    print(venueId)

    url = f"https://cricbuzz-cricket.p.rapidapi.com/venues/v1/{venueId}"

    headers = {
        "x-rapidapi-key": "c731246330msh7b7736b1d0af948p1083c6jsn55327cfb8111",
        "x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
    }

    try:
        response1 = requests.get(url, headers=headers, timeout=10)
        response1.raise_for_status()
        data2 = response1.json()
    except Exception as e:
        print("Error fetching:", venueId, e)
        data2 = {}

    ground = data2.get("ground")
    city = data2.get("city")

    cricket_matches.append({
        "venueId": venueId,
        "ground": ground,
        "city": city
    })

    print(ground)
    print(city)


291
JSCA International Stadium Complex
Ranchi
335
Shaheed Veer Narayan Singh International Stadium
Raipur
123
Manuka Oval
Canberra
93
Bir Sreshtho Flight Lieutenant Matiur Rahman Stadium
Chattogram
93
Bir Sreshtho Flight Lieutenant Matiur Rahman Stadium
Chattogram
371
Hagley Oval
Christchurch
394
Bayuemas Oval
Kuala Lumpur
394
Bayuemas Oval
Kuala Lumpur
767
La Manga Club Top Ground
Cartagena, Murcia
1444
St Albans Club
Corimayo, Buenos Aires
1444
St Albans Club
Corimayo, Buenos Aires
1444
St Albans Club
Corimayo, Buenos Aires
1444
St Albans Club
Corimayo, Buenos Aires
25
Rawalpindi Cricket Stadium
Rawalpindi
1438217
Nigeria Cricket Federation Oval 1
Abuja
1438217
Nigeria Cricket Federation Oval 1
Abuja
140
Sharjah Cricket Stadium
Sharjah
140
Sharjah Cricket Stadium
Sharjah
153
Dubai International Cricket Stadium
Dubai
153
Dubai International Cricket Stadium
Dubai
94
Sheikh Zayed Stadium
Abu Dhabi
94
Sheikh Zayed Stadium
Abu Dhabi
94
Sheikh Zayed Stadium
Abu Dhabi
94
Sheikh Zayed Stadiu

In [14]:
print(cricket_matches)

[{'venueId': 291, 'ground': 'JSCA International Stadium Complex', 'city': 'Ranchi'}, {'venueId': 335, 'ground': 'Shaheed Veer Narayan Singh International Stadium', 'city': 'Raipur'}, {'venueId': 123, 'ground': 'Manuka Oval', 'city': 'Canberra'}, {'venueId': 93, 'ground': 'Bir Sreshtho Flight Lieutenant Matiur Rahman Stadium', 'city': 'Chattogram'}, {'venueId': 93, 'ground': 'Bir Sreshtho Flight Lieutenant Matiur Rahman Stadium', 'city': 'Chattogram'}, {'venueId': 371, 'ground': 'Hagley Oval', 'city': 'Christchurch'}, {'venueId': 394, 'ground': 'Bayuemas Oval', 'city': 'Kuala Lumpur'}, {'venueId': 394, 'ground': 'Bayuemas Oval', 'city': 'Kuala Lumpur'}, {'venueId': 767, 'ground': 'La Manga Club Top Ground', 'city': 'Cartagena, Murcia'}, {'venueId': 1444, 'ground': 'St Albans Club', 'city': 'Corimayo, Buenos Aires'}, {'venueId': 1444, 'ground': 'St Albans Club', 'city': 'Corimayo, Buenos Aires'}, {'venueId': 1444, 'ground': 'St Albans Club', 'city': 'Corimayo, Buenos Aires'}, {'venueId':

In [25]:
import requests

url = "https://cricbuzz-cricket.p.rapidapi.com/venues/v1/45"

headers = {
	"x-rapidapi-key": "d5744f7de2msh90e1b4c46e5734ap186e68jsncacc1ce53688",
	"x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}

response = requests.get(url, headers=headers)
data2 = response.json()
ground = data2.get("ground")
city = data2.get("city")
print(ground)
print(city)

Basin Reserve
Wellington


Question 3 List the top 10 highest run scorers in ODI cricket. Show player name, total runs scored, batting average, and number of centuries. Display the highest run scorer first.

In [ ]:
import requests

cricket_matches =[]

for p in dataplayer.get("player"):
    player_id = p.get("id")
    name = p.get("name")

    url = f"https://cricbuzz-cricket.p.rapidapi.com/stats/v1/player/{player_id}/batting"
    headers = {
        "x-rapidapi-key": "574fc916a1msh15912192e35ecf8p1a22d1jsnfb52d5626fd6",
        "x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
    }

    response = requests.get(url, headers=headers)
    data1 = response.json()

    total_runs = None
    batting_avg = None
    centuries = None

    for row in data1.get("values", []):
        values = row.get("values", [])

        if not values:
            continue

        stat_name = values[0]

        if stat_name == "Runs":
            total_runs = values[2] 

        if stat_name == "Average":
            batting_avg = values[2] 

        if stat_name == "100s":
            centuries = values[2]  

    cricket_matches.append({
        "playerid": player_id,
        "name": name,
        "totalruns": total_runs,
        "battingavg": batting_avg,
        "centuries" : centuries
    })



In [17]:
import requests

url = "https://cricbuzz-cricket.p.rapidapi.com/teams/v1/2/players" #GET - teams/get-players

headers = {
	"x-rapidapi-key": "574fc916a1msh15912192e35ecf8p1a22d1jsnfb52d5626fd6",
	"x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}

response = requests.get(url, headers=headers)
dataplayer = response.json()
print(dataplayer)

{'player': [{'name': 'BATSMEN', 'imageId': 174146}, {'id': '11808', 'name': 'Shubman Gill', 'imageId': 616515, 'battingStyle': 'Right-hand bat', 'bowlingStyle': 'Right-arm offbreak'}, {'id': '13940', 'name': 'Yashasvi Jaiswal', 'imageId': 591942, 'battingStyle': 'Left-hand bat', 'bowlingStyle': 'Right-arm legbreak'}, {'id': '13866', 'name': 'Sai Sudharsan', 'imageId': 717782, 'battingStyle': 'Left-hand bat', 'bowlingStyle': 'Right-arm legbreak'}, {'id': '576', 'name': 'Rohit Sharma', 'imageId': 616514, 'battingStyle': 'Right-hand bat', 'bowlingStyle': 'Right-arm offbreak'}, {'id': '1413', 'name': 'Virat Kohli', 'imageId': 616517, 'battingStyle': 'Right-hand bat', 'bowlingStyle': 'Right-arm medium'}, {'id': '7915', 'name': 'Suryakumar Yadav', 'imageId': 352481, 'battingStyle': 'Right-hand bat', 'bowlingStyle': 'Right-arm offbreak'}, {'id': '9428', 'name': 'Shreyas Iyer', 'imageId': 616518, 'battingStyle': 'Right-hand bat', 'bowlingStyle': 'Right-arm legbreak'}, {'id': '10896', 'name': '

In [20]:
import psycopg2 as db

conn = db.connect(
    host="localhost",
    port="5432",
    dbname="Cricbuzz",
    user="postgres",
    password="Tanvikha@1998"
)
print("Connected to DB")

cursor = conn.cursor()

insert_query = """
    INSERT INTO odi_player_info_3
(player_id, player_name, total_runs, batting_avg, centuries)
VALUES
(%s, %s, %s, %s, %s);
"""

for match in cricket_matches:
    cursor.execute(insert_query, (
        match["playerid"],
        match["name"],
        match["totalruns"],
        match["battingavg"],
        match["centuries"]
    ))
conn.commit()
cursor.close()
conn.close()

print("Records inserted successfully!")


Connected to DB
Records inserted successfully!


Question 5 Calculate how many matches each team has won. Show team name and total number of wins. Display teams with the most wins first.

In [ ]:
import requests

team_types = ["international", "league", "women", "domestic"]

headers = {
    "x-rapidapi-key": "574fc916a1msh15912192e35ecf8p1a22d1jsnfb52d5626fd6",
    "x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}

team_list = []

for t in team_types:
    url = f"https://cricbuzz-cricket.p.rapidapi.com/teams/v1/{t}"

    response = requests.get(url, headers=headers)
    data = response.json()

    for item in data.get("list", []):
        team_id = item.get("teamId")
        team_name = item.get("teamName")

        if team_id:  
            team_list.append({
                "teamId": team_id,
                "teamName": team_name,
                "type": t
            })

for team in team_list:
    print(team["teamId"], team["teamName"], team["type"])


In [ ]:
import requests

team_wins = {}
team_results = []  

for team in team_list:
    team_id = team["teamId"]
    team_name = team["teamName"]

    print("Processing:", team_name, "ID:", team_id)

  
    url = f"https://cricbuzz-cricket.p.rapidapi.com/stats/v1/team/{team_id}"

    querystring = {"statsType": "mostWins"}

    headers = {
        "x-rapidapi-key": "574fc916a1msh15912192e35ecf8p1a22d1jsnfb52d5626fd6",
        "x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
    }

    response = requests.get(url, headers=headers, params=querystring)
    data2 = response.json()

    
    win_count = 0

    for block in data2.get("teamMatchesData", []):
        matches = block.get("matchDetailsMap", {}).get("match", [])

        for match in matches:
            info = match.get("matchInfo", {})
            status = info.get("status", "")

            
            if status.startswith(team_name):
                if "won" in status:
                    win_count += 1

    team_results.append({
        "teamId": team_id,
        "teamName": team_name,
        "wins": win_count
    })


print("\nFinal Team Wins:")
for row in team_results:
    print(row)


Processing: India ID: 2
Processing: Afghanistan ID: 96
Processing: Ireland ID: 27
Processing: Pakistan ID: 3
Processing: Australia ID: 4
Processing: Sri Lanka ID: 5
Processing: Bangladesh ID: 6
Processing: England ID: 9
Processing: West Indies ID: 10
Processing: South Africa ID: 11
Processing: Zimbabwe ID: 12
Processing: New Zealand ID: 13
Processing: Malaysia ID: 71
Processing: Nepal ID: 72
Processing: Germany ID: 77
Processing: Namibia ID: 161
Processing: Denmark ID: 185
Processing: Singapore ID: 190
Processing: Papua New Guinea ID: 287
Processing: Kuwait ID: 298
Processing: Vanuatu ID: 300
Processing: Jersey ID: 303
Processing: Oman ID: 304
Processing: Fiji ID: 343
Processing: Italy ID: 527
Processing: Botswana ID: 529
Processing: Belgium ID: 541
Processing: Uganda ID: 44
Processing: Canada ID: 26
Processing: United Arab Emirates ID: 7
Processing: Hong Kong, China ID: 8
Processing: Kenya ID: 14
Processing: United States of America ID: 15
Processing: Scotland ID: 23
Processing: Nethe

In [24]:
import psycopg2 as db

conn = db.connect(
    host="localhost",
    port="5432",
    dbname="Cricbuzz",
    user="postgres",
    password="Tanvikha@1998"
)
print("Connected to DB")

cursor = conn.cursor()

insert_query = """
    INSERT INTO team_wins_5 (team_id, team_name, win_count)
VALUES (%s, %s, %s)
ON CONFLICT (team_id)
DO UPDATE SET 
    team_name = EXCLUDED.team_name,
    win_count = EXCLUDED.win_count;
"""

for teams in team_results:
    cursor.execute(insert_query, (
        teams["teamId"],
        teams["teamName"],
        teams["wins"]
    ))
conn.commit()
cursor.close()
conn.close()

print("Records inserted successfully!")


Connected to DB
Records inserted successfully!


Question 7 Find the highest individual batting score achieved in each cricket format (Test, ODI, T20I). Display the format and the highest score for that format.

In [ ]:
import requests
headers = {
	"x-rapidapi-key": "574fc916a1msh15912192e35ecf8p1a22d1jsnfb52d5626fd6",
	"x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}
players_highest_scores = []

for p in dataplayer.get("player"):
    player_id = p.get("id")
    name = p.get("name")
    print(player_id)
    
    url = f"https://cricbuzz-cricket.p.rapidapi.com/stats/v1/player/{player_id}/batting"

    try:
        response = requests.get(url, headers=headers, timeout=10)
        response.raise_for_status() 
        data = response.json()  
        for row in data.get("values", []):
            if row.get("values", [])[0] == "Highest":
                players_highest_scores.append({
                    "playerId": player_id,
                    "Test": row["values"][1],
                    "ODI": row["values"][2],
                    "T20I": row["values"][3],
                    "IPL": row["values"][4]
                })
    except requests.exceptions.RequestException as e:
        print(f"HTTP error for player {player_id}: {e}")
    except ValueError as e:
        print(f"Invalid JSON for player {player_id}: {e}")

print(players_highest_scores)


In [36]:
players_highest_scores

[{'playerId': '11808',
  'Test': '269',
  'ODI': '208',
  'T20I': '126',
  'IPL': '129'},
 {'playerId': '13940',
  'Test': '214',
  'ODI': '116',
  'T20I': '100',
  'IPL': '124'},
 {'playerId': '13866', 'Test': '87', 'ODI': '62', 'T20I': '0', 'IPL': '108'},
 {'playerId': '576', 'Test': '212', 'ODI': '264', 'T20I': '121', 'IPL': '109'},
 {'playerId': '1413',
  'Test': '254',
  'ODI': '183',
  'T20I': '122',
  'IPL': '113'},
 {'playerId': '7915', 'Test': '8', 'ODI': '72', 'T20I': '117', 'IPL': '103'},
 {'playerId': '9428', 'Test': '105', 'ODI': '128', 'T20I': '74', 'IPL': '97'},
 {'playerId': '10896', 'Test': '0', 'ODI': '38', 'T20I': '69', 'IPL': '67'},
 {'playerId': '14504', 'Test': '0', 'ODI': '52', 'T20I': '120', 'IPL': '84'},
 {'playerId': '11813', 'Test': '0', 'ODI': '105', 'T20I': '123', 'IPL': '108'},
 {'playerId': '10636', 'Test': '32', 'ODI': '22', 'T20I': '0', 'IPL': '112'},
 {'playerId': '9429', 'Test': '150', 'ODI': '0', 'T20I': '0', 'IPL': '67'},
 {'playerId': '9716', 'Test

In [29]:
import requests

url = "https://cricbuzz-cricket.p.rapidapi.com/teams/v1/2/players" #GET - teams/get-players

headers = {
	"x-rapidapi-key": "574fc916a1msh15912192e35ecf8p1a22d1jsnfb52d5626fd6",
	"x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}

response = requests.get(url, headers=headers)
dataplayer = response.json()
print(dataplayer)

{'player': [{'name': 'BATSMEN', 'imageId': 174146}, {'id': '11808', 'name': 'Shubman Gill', 'imageId': 616515, 'battingStyle': 'Right-hand bat', 'bowlingStyle': 'Right-arm offbreak'}, {'id': '13940', 'name': 'Yashasvi Jaiswal', 'imageId': 591942, 'battingStyle': 'Left-hand bat', 'bowlingStyle': 'Right-arm legbreak'}, {'id': '13866', 'name': 'Sai Sudharsan', 'imageId': 717782, 'battingStyle': 'Left-hand bat', 'bowlingStyle': 'Right-arm legbreak'}, {'id': '576', 'name': 'Rohit Sharma', 'imageId': 616514, 'battingStyle': 'Right-hand bat', 'bowlingStyle': 'Right-arm offbreak'}, {'id': '1413', 'name': 'Virat Kohli', 'imageId': 616517, 'battingStyle': 'Right-hand bat', 'bowlingStyle': 'Right-arm medium'}, {'id': '7915', 'name': 'Suryakumar Yadav', 'imageId': 352481, 'battingStyle': 'Right-hand bat', 'bowlingStyle': 'Right-arm offbreak'}, {'id': '9428', 'name': 'Shreyas Iyer', 'imageId': 616518, 'battingStyle': 'Right-hand bat', 'bowlingStyle': 'Right-arm legbreak'}, {'id': '10896', 'name': '

In [37]:
import psycopg2 as db

conn = db.connect(
    host="localhost",
    port="5432",
    dbname="Cricbuzz",
    user="postgres",
    password="Tanvikha@1998"
)
print("Connected to DB")

cursor = conn.cursor()

insert_query = """
    INSERT INTO player_highest_scores_7 (player_id, test_score, odi_score, t20i_score, ipl_score)
    VALUES (%s, %s, %s, %s, %s)
    ON CONFLICT (player_id)
    DO UPDATE SET 
        test_score = EXCLUDED.test_score,
        odi_score = EXCLUDED.odi_score,
        t20i_score = EXCLUDED.t20i_score,
        ipl_score = EXCLUDED.ipl_score;
"""

for player in players_highest_scores:
    cursor.execute(insert_query, (
        player["playerId"],
        player["Test"],
        player["ODI"],
        player["T20I"],
        player["IPL"]
    ))

conn.commit()
cursor.close()
conn.close()
print("Records inserted successfully!")


Connected to DB
Records inserted successfully!



Question 8 Show all cricket series that started in the year 2024. Include series name, host country, match type, start date, and total number of matches planned.


In [28]:
import requests

url = "https://cricbuzz-cricket.p.rapidapi.com/series/v1/women"

headers = {
	"x-rapidapi-key": "7c824e1452mshf794a7d6643db91p14dcecjsn7d822c3778f1",
	"x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}

response = requests.get(url, headers=headers)
datax= response.json()
print(response.json())

{'seriesMapProto': [{'date': 'NOVEMBER 2025', 'series': [{'id': 10405, 'name': 'Womens Big Bash League 2025', 'startDt': '1762646400000', 'endDt': '1765584000000'}]}, {'date': 'DECEMBER 2025', 'series': [{'id': 10994, 'name': 'Ireland Women tour of South Africa 2025', 'startDt': '1764892800000', 'endDt': '1766102400000'}, {'id': 11342, 'name': 'Oman Womens T20I Tri Series 2025', 'startDt': '1764979200000', 'endDt': '1765324800000'}, {'id': 11350, 'name': 'GCC Womens T20I Championship, 2025', 'startDt': '1765497600000', 'endDt': '1766102400000'}, {'id': 11355, 'name': 'SEA Games Womens Twenty20 Cricket Competition 2025', 'startDt': '1765756800000', 'endDt': '1766102400000'}, {'id': 11262, 'name': 'Sri Lanka Women tour of India 2025', 'startDt': '1766275200000', 'endDt': '1767052800000'}]}, {'date': 'JANUARY 2026', 'series': [{'id': 11275, 'name': 'Womens Premier League 2026', 'startDt': '1767916800000', 'endDt': '1770249600000'}]}, {'date': 'FEBRUARY 2026', 'series': [{'id': 10146, 'nam

In [ ]:
import requests
import time

all_matches = []

headers = {
    "x-rapidapi-key": "7c824e1452mshf794a7d6643db91p14dcecjsn7d822c3778f1",
    "x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}

for series in series_list:

    start_date = series["start_date"]
    sid = series["id"]
    name = series["name"]

    url = f"https://cricbuzz-cricket.p.rapidapi.com/series/v1/{sid}"
    res2 = requests.get(url, headers=headers)

    if res2.status_code != 200:
        print(f"API failed for series {sid}")
        continue

    try:
        data = res2.json()
    except ValueError:
        print("Invalid JSON response")
        print(res2.text[:200])
        continue

    match_details = data.get("matchDetails", [])
    total_matches = 0

    for md in match_details:
        match_map = md.get("matchDetailsMap")
        if not match_map:
            continue

        matches = match_map.get("match", [])

        for match_entry in matches:
            match_info = match_entry.get("matchInfo", {})

            match_format = match_info.get("matchFormat", "Unknown")
            start_date1 = match_info.get("startDate")

            total_matches += 1

    all_matches.append({
        "series_id": sid,
        "series_name": name,
        "start_date" : start_date,
        "match_format": match_format,
        "total_no_of_matches": total_matches
    })


print(all_matches)


[{'series_id': 10405, 'series_name': 'Womens Big Bash League 2025', 'start_date': 'NOVEMBER 2025', 'match_format': 'T20', 'total_no_of_matches': 43}, {'series_id': 10994, 'series_name': 'Ireland Women tour of South Africa 2025', 'start_date': 'DECEMBER 2025', 'match_format': 'ODI', 'total_no_of_matches': 6}, {'series_id': 11342, 'series_name': 'Oman Womens T20I Tri Series 2025', 'start_date': 'DECEMBER 2025', 'match_format': 'T20', 'total_no_of_matches': 4}, {'series_id': 11350, 'series_name': 'GCC Womens T20I Championship, 2025', 'start_date': 'DECEMBER 2025', 'match_format': 'T20', 'total_no_of_matches': 16}, {'series_id': 11355, 'series_name': 'SEA Games Womens Twenty20 Cricket Competition 2025', 'start_date': 'DECEMBER 2025', 'match_format': 'T20', 'total_no_of_matches': 10}, {'series_id': 11262, 'series_name': 'Sri Lanka Women tour of India 2025', 'start_date': 'DECEMBER 2025', 'match_format': 'T20', 'total_no_of_matches': 5}, {'series_id': 11275, 'series_name': 'Womens Premier Le

In [ ]:
import requests
import time

series_list = []


seriesmapproto = datax.get("seriesMapProto", [])


for s in seriesmapproto:
    start_date = s.get("date")
    series = s.get("series", [])

    for ser in series:
        sid = ser.get("id")
        name = ser.get("name")

        series_list.append({"id": sid, "name": name,"start_date":start_date})
        print(f"data collecetd for {sid},{start_date}")

data collecetd for 10405,NOVEMBER 2025
data collecetd for 10994,DECEMBER 2025
data collecetd for 11342,DECEMBER 2025
data collecetd for 11350,DECEMBER 2025
data collecetd for 11355,DECEMBER 2025
data collecetd for 11262,DECEMBER 2025
data collecetd for 11275,JANUARY 2026
data collecetd for 10146,FEBRUARY 2026
data collecetd for 9611,FEBRUARY 2026
data collecetd for 10245,FEBRUARY 2026
data collecetd for 10251,MARCH 2026
data collecetd for 10526,MAY 2026
data collecetd for 10543,MAY 2026
data collecetd for 10119,JUNE 2026
data collecetd for 10548,AUGUST 2026


In [31]:
import psycopg2 as db

conn = db.connect(
    host="localhost",
    port="5432",
    dbname="Cricbuzz",
    user="postgres",
    password="Tanvikha@1998"
)

print("Connected to DB")

cursor = conn.cursor()

insert_query = """
    INSERT INTO cricket_series_8
    (series_id, series_name, match_type, start_date, total_matches)
    VALUES (%s, %s, %s, %s, %s)
"""

for match in all_matches:
    cursor.execute(insert_query, (
        match.get("series_id"),
        match.get("series_name"),
        match.get("match_format"),
        match.get("start_date"),
        match.get("total_no_of_matches")
    ))

conn.commit()
cursor.close()
conn.close()

print("Records inserted successfully!")


Connected to DB
Records inserted successfully!


Question 9 Find all-rounder players who have scored more than 1000 runs AND taken more than 50 wickets in their career. Display player name, total runs, total wickets, and the cricket format.

In [ ]:
import requests

team_list_id = []

url = "https://cricbuzz-cricket.p.rapidapi.com/teams/v1/international"

headers = {
	"x-rapidapi-key": "77fc4172d0msha36e7d9e491ec76p1d0e18jsna85cb569e36b",
	"x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}

response = requests.get(url, headers=headers)


if response.status_code == 200:
    data = response.json()
    teams = data.get("list", [])

    for team in teams:
        if "teamId" in team:
            team_list_id.append({"id": team["teamId"], "name": team.get("teamName")})

    print("Team IDs and Names:")
    for t in team_list_id:
        print(t)
else:
    print("API request failed with status:", response.status_code)


Team IDs and Names:
{'id': 2, 'name': 'India'}
{'id': 96, 'name': 'Afghanistan'}
{'id': 27, 'name': 'Ireland'}
{'id': 3, 'name': 'Pakistan'}
{'id': 4, 'name': 'Australia'}
{'id': 5, 'name': 'Sri Lanka'}
{'id': 6, 'name': 'Bangladesh'}
{'id': 9, 'name': 'England'}
{'id': 10, 'name': 'West Indies'}
{'id': 11, 'name': 'South Africa'}
{'id': 12, 'name': 'Zimbabwe'}
{'id': 13, 'name': 'New Zealand'}
{'id': 71, 'name': 'Malaysia'}
{'id': 72, 'name': 'Nepal'}
{'id': 77, 'name': 'Germany'}
{'id': 161, 'name': 'Namibia'}
{'id': 185, 'name': 'Denmark'}
{'id': 190, 'name': 'Singapore'}
{'id': 287, 'name': 'Papua New Guinea'}
{'id': 298, 'name': 'Kuwait'}
{'id': 300, 'name': 'Vanuatu'}
{'id': 303, 'name': 'Jersey'}
{'id': 304, 'name': 'Oman'}
{'id': 343, 'name': 'Fiji'}
{'id': 527, 'name': 'Italy'}
{'id': 529, 'name': 'Botswana'}
{'id': 541, 'name': 'Belgium'}
{'id': 44, 'name': 'Uganda'}
{'id': 26, 'name': 'Canada'}
{'id': 7, 'name': 'United Arab Emirates'}
{'id': 8, 'name': 'Hong Kong, China'}
{

In [51]:
print(team_list_id)

[{'id': 549, 'name': 'Argentina'}, {'id': 561, 'name': 'Czech Republic'}, {'id': 562, 'name': 'Saint Helena'}, {'id': 563, 'name': 'Maldives'}, {'id': 564, 'name': 'Gibraltar'}, {'id': 565, 'name': 'Myanmar'}, {'id': 566, 'name': 'Indonesia'}, {'id': 567, 'name': 'Gambia'}, {'id': 568, 'name': 'Swaziland'}, {'id': 569, 'name': 'Rwanda'}, {'id': 560, 'name': 'Brazil'}, {'id': 559, 'name': 'Sierra Leone'}, {'id': 550, 'name': 'Hungary'}, {'id': 551, 'name': 'Mozambique'}, {'id': 552, 'name': 'Chile'}, {'id': 553, 'name': 'Malawi'}, {'id': 554, 'name': 'Israel'}, {'id': 555, 'name': 'Bhutan'}, {'id': 556, 'name': 'Finland'}, {'id': 557, 'name': 'Isle of Man'}, {'id': 558, 'name': 'Bulgaria'}, {'id': 570, 'name': 'Lesotho'}, {'id': 571, 'name': 'Saudi Arabia'}, {'id': 578, 'name': 'Aakash Tigers MWS'}, {'id': 590, 'name': 'Kutch Warriors'}, {'id': 591, 'name': 'Brampton Wolves'}, {'id': 593, 'name': 'Kuwait U19'}, {'id': 595, 'name': 'Chandigarh'}, {'id': 596, 'name': 'Portugal'}, {'id': 6

In [ ]:
import requests
import time

team_players = []

headers = {
    "x-rapidapi-key": "77fc4172d0msha36e7d9e491ec76p1d0e18jsna85cb569e36b",
    "x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}

for team in team_list_id:
    team_id = team.get("id")

    if not team_id:
        continue

    url = f"https://cricbuzz-cricket.p.rapidapi.com/teams/v1/{team_id}/players"
    response = requests.get(url, headers=headers)

    if response.status_code != 200:
        print(f"API failed for team {team_id}: {response.status_code}")
        continue

    try:
        data = response.json()
    except ValueError:
        print(f"Invalid JSON for team {team_id}")
        continue

    players = data.get("player", [])

    for p in players:
        player_id = p.get("id")
        player_name = p.get("name")

        team_players.append({
            "team_id": team_id,
            "player_id": player_id,
            "player_name": player_name
        })

print("Team Players:")
for p in team_players:
    print(p)


In [58]:
print(team_players)

[{'team_id': 2, 'player_id': None, 'player_name': 'BATSMEN'}, {'team_id': 2, 'player_id': '11808', 'player_name': 'Shubman Gill'}, {'team_id': 2, 'player_id': '13940', 'player_name': 'Yashasvi Jaiswal'}, {'team_id': 2, 'player_id': '13866', 'player_name': 'Sai Sudharsan'}, {'team_id': 2, 'player_id': '576', 'player_name': 'Rohit Sharma'}, {'team_id': 2, 'player_id': '1413', 'player_name': 'Virat Kohli'}, {'team_id': 2, 'player_id': '7915', 'player_name': 'Suryakumar Yadav'}, {'team_id': 2, 'player_id': '9428', 'player_name': 'Shreyas Iyer'}, {'team_id': 2, 'player_id': '10896', 'player_name': 'Rinku Singh'}, {'team_id': 2, 'player_id': '14504', 'player_name': 'Tilak Varma'}, {'team_id': 2, 'player_id': '11813', 'player_name': 'Ruturaj Gaikwad'}, {'team_id': 2, 'player_id': '10636', 'player_name': 'Rajat Patidar'}, {'team_id': 2, 'player_id': '9429', 'player_name': 'Sarfaraz Khan'}, {'team_id': 2, 'player_id': '9716', 'player_name': 'Abhimanyu Easwaran'}, {'team_id': 2, 'player_id': '82

In [ ]:
import requests
import time

scores = []

headers = {
    "x-rapidapi-key": "77fc4172d0msha36e7d9e491ec76p1d0e18jsna85cb569e36b",
    "x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}

formats = {
    1: "TEST",
    2: "ODI",
    3: "T20",
    4: "IPL"
}

for p in team_players:

    player_id = p.get("player_id")
    player_name = p.get("player_name")
    team_id = p.get("team_id")

    if not player_id:
        continue

    role = None
    role_url = f"https://cricbuzz-cricket.p.rapidapi.com/stats/v1/player/{player_id}"
    role_res = requests.get(role_url, headers=headers)

    if role_res.status_code == 200:
        try:
            role_data = role_res.json()
            role = role_data.get("role")
        except ValueError:
            role = None

    runs = {}
    batting_url = f"https://cricbuzz-cricket.p.rapidapi.com/stats/v1/player/{player_id}/batting"
    bat_res = requests.get(batting_url, headers=headers)

    if bat_res.status_code == 200:
        try:
            bat_data = bat_res.json()
            for row in bat_data.get("values", []):
                vals = row.get("values", [])
                if vals and vals[0] == "Runs":
                    for i in range(1, 5):
                        runs[formats[i]] = int(vals[i]) if vals[i].isdigit() else 0
        except ValueError:
            pass

    wickets = {}
    bowling_url = f"https://cricbuzz-cricket.p.rapidapi.com/stats/v1/player/{player_id}/bowling"
    bowl_res = requests.get(bowling_url, headers=headers)

    if bowl_res.status_code == 200:
        try:
            bowl_data = bowl_res.json()
            for row in bowl_data.get("values", []):
                vals = row.get("values", [])
                if vals and vals[0] == "Wickets":
                    for i in range(1, 5):
                        wickets[formats[i]] = int(vals[i]) if vals[i].isdigit() else 0
        except ValueError:
            pass

    for fmt in formats.values():
        scores.append({
            "team_id": team_id,
            "player_id": player_id,
            "player_name": player_name,
            "format": fmt,
            "total_runs": runs.get(fmt, 0),
            "total_wickets": wickets.get(fmt, 0),
            "role": role
        })

print("Player Career Stats:")
for s in scores:
    print(s)


In [60]:
print(scores)

[{'team_id': 2, 'player_id': '11808', 'player_name': 'Shubman Gill', 'format': 'TEST', 'total_runs': 2843, 'total_wickets': 0, 'role': 'Batsman'}, {'team_id': 2, 'player_id': '11808', 'player_name': 'Shubman Gill', 'format': 'ODI', 'total_runs': 2818, 'total_wickets': 0, 'role': 'Batsman'}, {'team_id': 2, 'player_id': '11808', 'player_name': 'Shubman Gill', 'format': 'T20', 'total_runs': 841, 'total_wickets': 0, 'role': 'Batsman'}, {'team_id': 2, 'player_id': '11808', 'player_name': 'Shubman Gill', 'format': 'IPL', 'total_runs': 3866, 'total_wickets': 0, 'role': 'Batsman'}, {'team_id': 2, 'player_id': '13940', 'player_name': 'Yashasvi Jaiswal', 'format': 'TEST', 'total_runs': 2511, 'total_wickets': 0, 'role': 'Batsman'}, {'team_id': 2, 'player_id': '13940', 'player_name': 'Yashasvi Jaiswal', 'format': 'ODI', 'total_runs': 171, 'total_wickets': 0, 'role': 'Batsman'}, {'team_id': 2, 'player_id': '13940', 'player_name': 'Yashasvi Jaiswal', 'format': 'T20', 'total_runs': 723, 'total_wicket

In [ ]:
import psycopg2 as db

conn = db.connect(
    host="localhost",
    port="5432",
    dbname="Cricbuzz",
    user="postgres",
    password="Tanvikha@1998"
)

print("Connected to DB")

cursor = conn.cursor()

insert_query = """
INSERT INTO player_career_stats_9
(player_id, player_name, cricket_format, total_runs, total_wickets, role)
VALUES (%s, %s, %s, %s, %s, %s);
"""

for s in scores:
    cursor.execute(insert_query, (
        s.get("player_id"),
        s.get("player_name"),
        s.get("format"),         
        s.get("total_runs"),
        s.get("total_wickets"),
        s.get("role")
    ))

conn.commit()
cursor.close()
conn.close()

print("Records inserted successfully!")


Connected to DB
Records inserted successfully!


Question 10 Get details of the last 20 completed matches. Show match description, both team names, winning team, victory margin, victory type (runs/wickets), and venue name. Display the most recent matches first.

In [ ]:
import requests

url = "https://cricbuzz-cricket.p.rapidapi.com/matches/v1/recent"

headers = {
    "x-rapidapi-key": "d63331dda4mshdc6a08299933a4fp1da5e1jsn89d940c6d2ed",
    "x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}

response = requests.get(url, headers=headers)
data = response.json()

last_20_completed_matches = []

for match_type in data.get("typeMatches", []):
    for series in match_type.get("seriesMatches", []):
        series_wrapper = series.get("seriesAdWrapper")
        if not series_wrapper:
            continue

        for match in series_wrapper.get("matches", []):
            match_info = match.get("matchInfo", {})

           
            if match_info.get("state") != "Complete":
                continue

            status = match_info.get("status", "")

            winning_team = None
            victory_margin = None
            victory_type = None

            if "won by" in status:
                winning_team = status.split(" won by ")[0]
                margin = status.split(" won by ")[1]

                if "runs" in margin:
                    victory_margin = margin.replace(" runs", "")
                    victory_type = "runs"
                elif "wkts" in margin:
                    victory_margin = margin.replace(" wkts", "")
                    victory_type = "wickets"

            last_20_completed_matches.append({
                "match_description": match_info.get("matchDesc"),
                "team1": match_info.get("team1", {}).get("teamName"),
                "team2": match_info.get("team2", {}).get("teamName"),
                "winning_team": winning_team,
                "victory_margin": victory_margin,
                "victory_type": victory_type,
                "venue": match_info.get("venueInfo", {}).get("ground"),
                "end_date": int(match_info.get("endDate", 0))
            })
last_20_completed_matches.sort(key=lambda x: x["end_date"], reverse=True)

last_20_completed_matches = last_20_completed_matches[:20]

print(last_20_completed_matches)


[]


In [69]:
import psycopg2 as db
import re

def extract_number(value):
    if not value:
        return None
    match = re.search(r'\d+', str(value))
    return int(match.group()) if match else None

conn = db.connect(
    host="localhost",
    port="5432",
    dbname="Cricbuzz",
    user="postgres",
    password="Tanvikha@1998"
)

print("Connected to DB")

cursor = conn.cursor()

insert_query = """
INSERT INTO recent_completed_matches_10
(
    match_description,
    team1_name,
    team2_name,
    winning_team,
    victory_margin,
    victory_type,
    venue_name,
    match_end_date
)
VALUES (%s, %s, %s, %s, %s, %s, %s, %s);
"""

for m in last_20_completed_matches:
    cursor.execute(insert_query, (
        m.get("match_description"),
        m.get("team1"),
        m.get("team2"),
        m.get("winning_team"),
        extract_number(m.get("victory_margin")),
        m.get("victory_type"),
        m.get("venue"),
        m.get("end_date")
    ))

conn.commit()
cursor.close()
conn.close()

print("Recent completed matches inserted successfully!")


Connected to DB
Recent completed matches inserted successfully!


Question 12 Analyze each international team's performance when playing at home versus playing away. Determine whether each team played at home or away based on whether the venue country matches the team's country. Count wins for each team in both home and away conditions.

In [40]:
import requests

url = "https://cricbuzz-cricket.p.rapidapi.com/matches/v1/recent"

headers = {
    "x-rapidapi-key": "d63331dda4mshdc6a08299933a4fp1da5e1jsn89d940c6d2ed",
    "x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}

response = requests.get(url, headers=headers)
data = response.json()


In [41]:
matches = []

for match_type in data.get("typeMatches", []):
    if match_type.get("matchType") != "International":
        continue

    for series in match_type.get("seriesMatches", []):
        wrapper = series.get("seriesAdWrapper")
        if not wrapper:
            continue

        for match in wrapper.get("matches", []):
            info = match.get("matchInfo", {})

            if info.get("state") != "Complete":
                continue

            status = info.get("status", "")

            winning_team = None
            if "won by" in status:
                winning_team = status.split(" won by ")[0]

            matches.append({
                "team1": info.get("team1", {}).get("teamName"),
                "team2": info.get("team2", {}).get("teamName"),
                "winning_team": winning_team,
                "venue": info.get("venueInfo", {}).get("ground")
            })


In [42]:
print(matches)

[]


In [ ]:
import requests

url = "https://cricbuzz-cricket.p.rapidapi.com/teams/v1/international"

headers = {
    "x-rapidapi-key": "d63331dda4mshdc6a08299933a4fp1da5e1jsn89d940c6d2ed",
    "x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}

response = requests.get(url, headers=headers)
data = response.json()

print(data)
teams = []

for team in data.get("list", []):
    team_name = team.get("teamName")

    teams.append({
        "team_name": team_name,
        "country_name": team_name 
    })

import psycopg2

conn = psycopg2.connect(
    host="localhost",
    port="5432",
    dbname="Cricbuzz",
    user="postgres",
    password="Tanvikha@1998"
)

cursor = conn.cursor()

insert_query = """
INSERT INTO team_country_mapping_12 (team_name, country_name)
VALUES (%s, %s)
ON CONFLICT (team_name) DO NOTHING;
"""

for t in teams:
    cursor.execute(insert_query, (
        t["team_name"],
        t["country_name"]
    ))

conn.commit()
cursor.close()
conn.close()

print("Team-country mapping inserted successfully!")


{'list': [{'teamName': 'Test Teams'}, {'teamId': 2, 'teamName': 'India', 'teamSName': 'IND', 'imageId': 776162, 'countryName': 'India'}, {'teamId': 96, 'teamName': 'Afghanistan', 'teamSName': 'AFG', 'imageId': 776177}, {'teamId': 27, 'teamName': 'Ireland', 'teamSName': 'IRE', 'imageId': 776285}, {'teamId': 3, 'teamName': 'Pakistan', 'teamSName': 'PAK', 'imageId': 776308, 'countryName': 'Pakistan'}, {'teamId': 4, 'teamName': 'Australia', 'teamSName': 'AUS', 'imageId': 776202, 'countryName': 'Australia'}, {'teamId': 5, 'teamName': 'Sri Lanka', 'teamSName': 'SL', 'imageId': 776254, 'countryName': 'Sri Lanka'}, {'teamId': 6, 'teamName': 'Bangladesh', 'teamSName': 'BAN', 'imageId': 776210}, {'teamId': 9, 'teamName': 'England', 'teamSName': 'ENG', 'imageId': 776237}, {'teamId': 10, 'teamName': 'West Indies', 'teamSName': 'WI', 'imageId': 776191}, {'teamId': 11, 'teamName': 'South Africa', 'teamSName': 'RSA', 'imageId': 776287}, {'teamId': 12, 'teamName': 'Zimbabwe', 'teamSName': 'ZIM', 'imag

Question 13 Identify batting partnerships where two consecutive batsmen (batting positions next to each other) scored a combined total of 100 or more runs in the same innings. Show both player names, their combined partnership runs, and which innings it occurred in.

In [ ]:
import requests

url = "https://cricbuzz-cricket.p.rapidapi.com/series/v1/international"

headers = {
    "x-rapidapi-key": "54cc6838efmshc791f44fbc850d6p18dcb0jsn45462fc0404c",
    "x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}

response = requests.get(url, headers=headers)
data = response.json()

series_ids = []

for month_block in data.get("seriesMapProto", []):
    for series in month_block.get("series", []):
        series_id = series.get("id")
        if series_id:
            series_ids.append(series_id)

print("Valid series IDs:", series_ids)


Valid series IDs: [7572, 10102, 10774, 11331, 9551, 11429, 11273, 11253, 10234, 10559, 10532, 10565, 10576]


In [ ]:
import requests

headers = {
    "x-rapidapi-key": "54cc6838efmshc791f44fbc850d6p18dcb0jsn45462fc0404c",
    "x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}

all_matches = []

for series_id in series_ids:
    url = f"https://cricbuzz-cricket.p.rapidapi.com/series/v1/{series_id}"
    response = requests.get(url, headers=headers)
    data = response.json()

    for item in data.get("matchDetails", []):
        match_map = item.get("matchDetailsMap")

        if not match_map:
            continue

        matches = match_map.get("match", [])
        for match in matches:
            match_info = match.get("matchInfo")
            if not match_info:
                continue

            venue_info = match_info.get("venueInfo", {})
            city = venue_info.get("city")
            ground = venue_info.get("ground")

            match_id = match_info.get("matchId")
            if match_id:
                all_matches.append({
                    "matchId": match_id,
                    "city": city,
                    "ground": ground
                })

print("Total matches fetched:", len(all_matches))
for m in all_matches:
    print(m)


Total matches fetched: 196
{'matchId': 89241, 'city': 'Kirtipur', 'ground': 'Tribhuvan University International Cricket Ground'}
{'matchId': 89248, 'city': 'Kirtipur', 'ground': 'Tribhuvan University International Cricket Ground'}
{'matchId': 89252, 'city': 'Kirtipur', 'ground': 'Tribhuvan University International Cricket Ground'}
{'matchId': 89259, 'city': 'Kirtipur', 'ground': 'Tribhuvan University International Cricket Ground'}
{'matchId': 89262, 'city': 'Kirtipur', 'ground': 'Tribhuvan University International Cricket Ground'}
{'matchId': 89269, 'city': 'Kirtipur', 'ground': 'Tribhuvan University International Cricket Ground'}
{'matchId': 89273, 'city': 'Dubai', 'ground': 'Dubai International Cricket Stadium'}
{'matchId': 89276, 'city': 'Dubai', 'ground': 'Dubai International Cricket Stadium'}
{'matchId': 89280, 'city': 'Dubai', 'ground': 'Dubai International Cricket Stadium'}
{'matchId': 89287, 'city': 'Dubai', 'ground': 'Dubai International Cricket Stadium'}
{'matchId': 89290, 'c

In [20]:
detailed_matches = []

for matchId in all_matches:
    mid = matchId.get("matchId")
    url = f"https://cricbuzz-cricket.p.rapidapi.com/mcenter/v1/{mid}/scard"
    headers = {
	"x-rapidapi-key": "d63331dda4mshdc6a08299933a4fp1da5e1jsn89d940c6d2ed",
	"x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}

response = requests.get(url, headers=headers)

print(response.json())
print("Fetched detailed scorecards for matches.")


{'scorecard': [], 'ismatchcomplete': False, 'appindex': {'seotitle': 'Cricket scorecard - ENG vs SL 3rd ODI,Sri Lanka tour of England, 2026 | Cricbuzz.com', 'weburl': 'http://www.cricbuzz.com/live-cricket-scorecard/129651/eng-vs-sl-3rd-odi-sri-lanka-tour-of-england-2026'}, 'status': 'Match starts at Sep 27, 09:30 GMT', 'responselastupdated': 1769430639}
Fetched detailed scorecards for matches.


In [ ]:
import psycopg2

conn = psycopg2.connect(
    host="localhost",
    port="5432",
    dbname="Cricbuzz",
    user="postgres",
    password="Tanvikha@1998"
)
cursor = conn.cursor()
print("DB connected")
insert_query = """
INSERT INTO batting_partnerships_13
(match_id, innings, player1, player2, partnership_runs)
VALUES (%s, %s, %s, %s, %s)
"""

for scorecard in detailed_matches:
    match_id = scorecard.get("matchInfo", {}).get("matchId")
    if not match_id:
        continue

    for inning in scorecard.get("innings", []):
        inning_number = inning.get("number") 
        partnerships = inning.get("partnerships", [])

        for partnership in partnerships:
            player1 = partnership.get("batsmen", [None, None])[0]
            player2 = partnership.get("batsmen", [None, None])[1]
            partnership_runs = partnership.get("partnership", 0)

            cursor.execute(insert_query, (
                match_id,
                inning_number,
                player1,
                player2,
                partnership_runs
            ))

conn.commit()
cursor.close()
conn.close()
print ("values added")

DB connected
values added


Question 14 Examine bowling performance at different venues. For bowlers who have played at least 3 matches at the same venue, calculate their average economy rate, total wickets taken, and number of matches played at each venue. Focus on bowlers who bowled at least 4 overs in each match.

In [ ]:
import requests

BASE_URL = "https://cricbuzz-cricket.p.rapidapi.com"

headers = {
    "x-rapidapi-key": "54cc6838efmshc791f44fbc850d6p18dcb0jsn45462fc0404c",
    "x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}

def overs_to_float(overs_str):
    if "." not in overs_str:
        return float(overs_str)
    overs, balls = overs_str.split(".")
    return int(overs) + int(balls) / 6

raw_bowling_rows = []

for match in all_matches:
    match_id = match["matchId"]
    venue = match["ground"] 

    url = f"{BASE_URL}/mcenter/v1/{match_id}/scard"
    response = requests.get(url, headers=headers)
    data = response.json()

    innings_list = data.get("scorecard", [])

    for innings in innings_list:
        bowlers = innings.get("bowler", [])

        for bowler in bowlers:
            overs_str = str(bowler.get("overs", "0"))
            overs = overs_to_float(overs_str)

            if overs < 4:
                continue

            raw_bowling_rows.append({
                "match_id": match_id,
                "venue": venue,
                "bowler_name": bowler.get("name"),
                "overs_bowled": round(overs, 1),
                "runs_conceded": bowler.get("runs", 0),
                "wickets_taken": bowler.get("wickets", 0)
            })

for row in raw_bowling_rows:
    print(row)


{'match_id': 89241, 'venue': 'Tribhuvan University International Cricket Ground', 'bowler_name': 'Trumpelmann', 'overs_bowled': 10.0, 'runs_conceded': 35, 'wickets_taken': 2}
{'match_id': 89241, 'venue': 'Tribhuvan University International Cricket Ground', 'bowler_name': 'Jack Brassell', 'overs_bowled': 5.0, 'runs_conceded': 11, 'wickets_taken': 2}
{'match_id': 89241, 'venue': 'Tribhuvan University International Cricket Ground', 'bowler_name': 'Tangeni Lungameni', 'overs_bowled': 4.0, 'runs_conceded': 18, 'wickets_taken': 0}
{'match_id': 89241, 'venue': 'Tribhuvan University International Cricket Ground', 'bowler_name': 'Bernard Scholtz', 'overs_bowled': 10.0, 'runs_conceded': 24, 'wickets_taken': 0}
{'match_id': 89241, 'venue': 'Tribhuvan University International Cricket Ground', 'bowler_name': 'Gerhard Erasmus', 'overs_bowled': 8.2, 'runs_conceded': 28, 'wickets_taken': 5}
{'match_id': 89241, 'venue': 'Tribhuvan University International Cricket Ground', 'bowler_name': 'Sompal Kami', 

In [19]:
print(raw_bowling_rows)

[{'match_id': 89241, 'venue': 'Tribhuvan University International Cricket Ground', 'bowler_name': 'Trumpelmann', 'overs_bowled': 10.0, 'runs_conceded': 35, 'wickets_taken': 2}, {'match_id': 89241, 'venue': 'Tribhuvan University International Cricket Ground', 'bowler_name': 'Jack Brassell', 'overs_bowled': 5.0, 'runs_conceded': 11, 'wickets_taken': 2}, {'match_id': 89241, 'venue': 'Tribhuvan University International Cricket Ground', 'bowler_name': 'Tangeni Lungameni', 'overs_bowled': 4.0, 'runs_conceded': 18, 'wickets_taken': 0}, {'match_id': 89241, 'venue': 'Tribhuvan University International Cricket Ground', 'bowler_name': 'Bernard Scholtz', 'overs_bowled': 10.0, 'runs_conceded': 24, 'wickets_taken': 0}, {'match_id': 89241, 'venue': 'Tribhuvan University International Cricket Ground', 'bowler_name': 'Gerhard Erasmus', 'overs_bowled': 8.2, 'runs_conceded': 28, 'wickets_taken': 5}, {'match_id': 89241, 'venue': 'Tribhuvan University International Cricket Ground', 'bowler_name': 'Sompal K

In [ ]:
import psycopg2


conn = psycopg2.connect(
    host="localhost",
    port="5432",
    dbname="Cricbuzz",
    user="postgres",
    password="Tanvikha@1998"
)

cursor = conn.cursor()
print("DB connected")

insert_query = """
INSERT INTO bowling_match_stats_14
(match_id, venue, bowler_name, overs_bowled, runs_conceded, wickets_taken)
VALUES (%s, %s, %s, %s, %s, %s)
ON CONFLICT (match_id, bowler_name) DO NOTHING;
"""

for row in raw_bowling_rows:
    cursor.execute(
        insert_query,
        (
            row["match_id"],
            row["venue"],
            row["bowler_name"],
            row["overs_bowled"],
            row["runs_conceded"],
            row["wickets_taken"]
        )
    )

conn.commit()
cursor.close()
conn.close()

print("Values added successfully")


DB connected
Values added successfully


Question 15 Identify players who perform exceptionally well in close matches. A close match is defined as one decided by less than 50 runs OR less than 5 wickets. For these close matches, calculate each player's average runs scored, total close matches played, and how many of those close matches their team won when they batted.

In [3]:
import requests
from collections import defaultdict
RAPIDAPI_KEY = "a9b22870fdmsh7b4355fda631462p1c2211jsn33d1b0124495"
RAPIDAPI_HOST = "cricbuzz-cricket.p.rapidapi.com"

HEADERS = {
    "X-RapidAPI-Key": RAPIDAPI_KEY,
    "X-RapidAPI-Host": RAPIDAPI_HOST
}

BASE_URL = "https://cricbuzz-cricket.p.rapidapi.com"

def get_completed_matches():
    
    url = f"{BASE_URL}/matches/v1/recent"
    response = requests.get(url, headers=HEADERS)
    response.raise_for_status()
    data = response.json()

    completed_matches = []

    for match_type in data.get("typeMatches", []):
        for series in match_type.get("seriesMatches", []):
            for match in series.get("seriesAdWrapper", {}).get("matches", []):
                if match.get("matchInfo", {}).get("state") == "Complete":
                    completed_matches.append(match["matchInfo"]["matchId"])

    return completed_matches


def get_match_scorecard(match_id):
    
    url = f"{BASE_URL}/mcenter/v1/{match_id}/scard"
    response = requests.get(url, headers=HEADERS)
    response.raise_for_status()
    return response.json()


def is_close_match(match_data):
   
    result = match_data.get("status", "").lower()

    if "run" in result:
        runs = int("".join(filter(str.isdigit, result)))
        return runs < 50
    if "wicket" in result:
        wickets = int("".join(filter(str.isdigit, result)))
        return wickets < 5

    return False


def analyze_close_matches():
    player_stats = defaultdict(lambda: {
        "player_name": "",
        "total_runs": 0,
        "close_matches_played": 0,
        "close_matches_won": 0
    })

    match_ids = get_completed_matches()

    for match_id in match_ids:
        match_data = get_match_scorecard(match_id)

        if not is_close_match(match_data):
            continue

        winning_team = match_data.get("matchHeader", {}).get("result", {}).get("winningTeam")

        for inning in match_data.get("scoreCard", []):
            batting_team = inning.get("batTeamDetails", {}).get("batTeamName")

            for player_id, batter in inning.get("batTeamDetails", {}).get("batsmenData", {}).items():
                runs = batter.get("runs", 0)
                player_name = batter.get("batName")

                player_stats[player_id]["player_name"] = player_name
                player_stats[player_id]["total_runs"] += runs
                player_stats[player_id]["close_matches_played"] += 1

                if batting_team == winning_team:
                    player_stats[player_id]["close_matches_won"] += 1

    result_list = []

    for stats in player_stats.values():
        avg_runs = (
            stats["total_runs"] / stats["close_matches_played"]
            if stats["close_matches_played"] > 0 else 0
        )

        result_list.append({
            "player_name": stats["player_name"],
            "average_runs_close_matches": round(avg_runs, 2),
            "close_matches_played": stats["close_matches_played"],
            "close_matches_won_when_batting": stats["close_matches_won"]
        })

    return result_list

if __name__ == "__main__":
    close_match_player_stats = analyze_close_matches()

    for player in close_match_player_stats:
        print(player)


In [ ]:
import requests

url = "https://cricbuzz-cricket.p.rapidapi.com/matches/v1/recent"

headers = {
	"x-rapidapi-key": "f27f2ae721msha6aa41349c7a3b9p1ce799jsn2753be900483",
	"x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}

response = requests.get(url, headers=headers)
data = response.json()
print(response.json())
matches = []



{'typeMatches': [{'matchType': 'International', 'seriesMatches': [{'seriesAdWrapper': {'seriesId': 9107, 'seriesName': 'The Ashes, 2025-26', 'matches': [{'matchInfo': {'matchId': 108809, 'seriesId': 9107, 'seriesName': 'The Ashes, 2025-26', 'matchDesc': '4th Test', 'matchFormat': 'TEST', 'startDate': '1766705400000', 'endDate': '1767076200000', 'state': 'Complete', 'status': 'England won by 4 wkts', 'team1': {'teamId': 4, 'teamName': 'Australia', 'teamSName': 'AUS', 'imageId': 776202}, 'team2': {'teamId': 9, 'teamName': 'England', 'teamSName': 'ENG', 'imageId': 776237}, 'venueInfo': {'id': 87, 'ground': 'Melbourne Cricket Ground', 'city': 'Melbourne', 'timezone': '+11:00', 'latitude': '-37.819967', 'longitude': '144.983449'}, 'currBatTeamId': 9, 'seriesStartDt': '1763683200000', 'seriesEndDt': '1768003200000', 'isTimeAnnounced': True, 'stateTitle': 'ENG Won'}, 'matchScore': {'team1Score': {'inngs1': {'inningsId': 1, 'runs': 152, 'wickets': 10, 'overs': 45.2}, 'inngs2': {'inningsId': 3,

In [85]:
matchesId = []

for match_type in data.get("typeMatches", []):
  for series in match_type.get("seriesMatches", []):
    seriesad = series.get("seriesAdWrapper",{})
    for matches in seriesad.get("matches",[]):
      matchInfo = matches.get("matchInfo",{})
      if matchInfo.get("state")=="Complete":
          status = matchInfo.get("status", "")
          if " won" in status.lower():
                winner = status.split(" won")[0]
          else:
                winner = None 
          matchesId.append({"matchId": matchInfo.get("matchId"),"status": winner,"startDate": matchInfo.get("startDate")})
          continue
          
      print(matchesId)
      

In [86]:
matchesId

[{'matchId': 108809, 'status': 'England', 'startDate': '1766705400000'},
 {'matchId': 137325, 'status': 'Bhutan', 'startDate': '1766979000000'},
 {'matchId': 141537, 'status': 'Indonesia', 'startDate': '1766971800000'},
 {'matchId': 126460, 'status': None, 'startDate': '1767454200000'},
 {'matchId': 126449, 'status': None, 'startDate': '1767438000000'},
 {'matchId': 126471, 'status': 'Paarl Royals', 'startDate': '1767533400000'},
 {'matchId': 126438, 'status': 'Paarl Royals', 'startDate': '1767367800000'},
 {'matchId': 126411,
  'status': 'Joburg Super Kings',
  'startDate': '1767108600000'},
 {'matchId': 126433,
  'status': 'Match tied (Joburg Super Kings',
  'startDate': '1767281400000'},
 {'matchId': 126427,
  'status': 'Pretoria Capitals',
  'startDate': '1767195000000'},
 {'matchId': 126422, 'status': 'Paarl Royals', 'startDate': '1767178800000'},
 {'matchId': 126400,
  'status': 'Sunrisers Eastern Cape',
  'startDate': '1767022200000'},
 {'matchId': 123254,
  'status': 'Hobart Hu

In [82]:
import requests
from collections import defaultdict
import re
player_stats = defaultdict(lambda: {
    "player_name": "",
    "total_runs": 0,
    "close_matches_played": 0,
    "close_matches_won": 0
})

for item in matchesId[:30]:
    match_id = item["matchId"]
    winning_team = item["status"]

    if not winning_team:
        continue

    scorecard_url = f"https://cricbuzz-cricket.p.rapidapi.com/mcenter/v1/{match_id}/scard"
    response = requests.get(scorecard_url, headers=HEADERS)
    data2 = response.json()

    players_counted = set()

    for inning in data2.get("scorecard", []):
        bat_team = inning.get("batteamname", "")
        batsmen = inning.get("batsman", [])

        for batter in batsmen:
            player_id = batter.get("id")
            player_name = batter.get("name")
            runs = batter.get("runs", 0)

            if not player_id:
                continue

            player_stats[player_id]["player_name"] = player_name
            player_stats[player_id]["total_runs"] += runs

            if player_id not in players_counted:
                player_stats[player_id]["close_matches_played"] += 1

                if bat_team.lower() == winning_team.lower():
                    player_stats[player_id]["close_matches_won"] += 1

                players_counted.add(player_id)

result_list = []

for stats in player_stats.values():
    avg_runs = (
        stats["total_runs"] / stats["close_matches_played"]
        if stats["close_matches_played"] > 0 else 0
    )

    result_list.append({
        "player_name": stats["player_name"],
        "average_runs_close_matches": round(avg_runs, 2),
        "close_matches_played": stats["close_matches_played"],
        "close_matches_won_when_batting": stats["close_matches_won"],
        "bat_team" : bat_team
    })

print(result_list)


[{'player_name': 'Head', 'average_runs_close_matches': 58.0, 'close_matches_played': 1, 'close_matches_won_when_batting': 0, 'bat_team': 'Rangpur Riders'}, {'player_name': 'Jake Weatherald', 'average_runs_close_matches': 15.0, 'close_matches_played': 1, 'close_matches_won_when_batting': 0, 'bat_team': 'Rangpur Riders'}, {'player_name': 'Labuschagne', 'average_runs_close_matches': 14.0, 'close_matches_played': 1, 'close_matches_won_when_batting': 0, 'bat_team': 'Rangpur Riders'}, {'player_name': 'Steven Smith', 'average_runs_close_matches': 33.0, 'close_matches_played': 1, 'close_matches_won_when_batting': 0, 'bat_team': 'Rangpur Riders'}, {'player_name': 'Khawaja', 'average_runs_close_matches': 29.0, 'close_matches_played': 1, 'close_matches_won_when_batting': 0, 'bat_team': 'Rangpur Riders'}, {'player_name': 'Alex Carey', 'average_runs_close_matches': 24.0, 'close_matches_played': 1, 'close_matches_won_when_batting': 0, 'bat_team': 'Rangpur Riders'}, {'player_name': 'Green', 'average_

In [ ]:
import requests

headers = {
	"x-rapidapi-key": "f27f2ae721msha6aa41349c7a3b9p1ce799jsn2753be900483",
	"x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}

for item in matchesId:
    match_id = item["matchId"]

    url = f"https://cricbuzz-cricket.p.rapidapi.com/mcenter/v1/{match_id}/scard"
    response = requests.get(url, headers=headers)
    data2 = response.json()
    print(data2)

In [ ]:
import psycopg2

conn = psycopg2.connect(
    host="localhost",
    port="5432",
    dbname="Cricbuzz",
    user="postgres",
    password="Tanvikha@1998"
)

cursor = conn.cursor()
print("DB connected")

insert_query = """
INSERT INTO close_match_player_performance_15
(player_name, bat_team, average_runs_close_matches, close_matches_played, close_matches_won_when_batting)
VALUES (%s, %s, %s, %s, %s)
"""

for r in result_list:
    cursor.execute(
        insert_query,
        (
            r["player_name"],
            r["bat_team"],
            r["average_runs_close_matches"],
            r["close_matches_played"],
            r["close_matches_won_when_batting"]
        )
    )

conn.commit()
cursor.close()
conn.close()

print("Values added successfully")


DB connected
Values added successfully


Question 16 Track how players' batting performance changes over different years. For matches since 2020, show each player's average runs per match and average strike rate for each year. Only include players who played at least 5 matches in that year.

In [ ]:
import requests
from collections import defaultdict
from datetime import datetime
player_stats_by_year = defaultdict(lambda: {
    "runs": 0,
    "balls": 0,
    "matches": 0
})

for item in matchesId:
    match_id = item["matchId"]
    start_date_ms = item.get("startDate") 
    if not start_date_ms:
        continue

    try:
     start_date_ms = int(start_date_ms)
    except ValueError:
     continue 

    year = datetime.fromtimestamp(start_date_ms / 1000.0).year
    if year < 2020:
     continue

    url = "https://cricbuzz-cricket.p.rapidapi.com/mcenter/v1/{match_id}/scard"

    headers = {
	"x-rapidapi-key": "f27f2ae721msha6aa41349c7a3b9p1ce799jsn2753be900483",
	"x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
           }

    response = requests.get(url, headers=headers)
    match_data = response.json()

    for inning in match_data.get("scorecard", []):
        batsmen = inning.get("batsman", [])

        counted_players = set()

        for batter in batsmen:
            pid = batter.get("id")
            name = batter.get("name")
            runs = batter.get("runs", 0)
            balls = batter.get("balls", 0)

            if not pid:
                continue

            key = (pid, year)

            player_stats_by_year[key]["runs"] += runs
            player_stats_by_year[key]["balls"] += balls

            if key not in counted_players:
                player_stats_by_year[key]["matches"] += 1
                player_stats_by_year[key]["player_name"] = name
                counted_players.add(key)


result = []

for (pid, y), stats in player_stats_by_year.items():
    if stats["matches"] < 5:
        continue

    avg_runs = stats["runs"] / stats["matches"]
    avg_strike_rate = (stats["runs"] / stats["balls"]) * 100 if stats["balls"] > 0 else 0

    result.append({
        "player_id": pid,
        "player_name": stats["player_name"],
        "year": y,
        "matches_played": stats["matches"],
        "average_runs": round(avg_runs, 2),
        "average_strike_rate": round(avg_strike_rate, 2)
    })

for rec in sorted(result, key=lambda x: (x["year"], -x["average_runs"])):
    print(rec)


In [ ]:
import psycopg2

conn = psycopg2.connect(
    host="localhost",
    port="5432",
    dbname="Cricbuzz",
    user="postgres",
    password="Tanvikha@1998"
)

cursor = conn.cursor()
print("DB connected")

insert_query = """
INSERT INTO player_yearly_batting_performance
(player_id, player_name, year, matches_played, average_runs_per_match, average_strike_rate)
VALUES (%s, %s, %s, %s, %s, %s)
"""

for r in yearly_result_list:
    cursor.execute(
        insert_query,
        (
            r["player_id"],
            r["player_name"],
            r["year"],
            r["matches_played"],
            r["average_runs"],
            r["average_strike_rate"]
        )
    )

conn.commit()
cursor.close()
conn.close()

print("Question 16 values added successfully")


Question 17 Investigate whether winning the toss gives teams an advantage in winning matches. Calculate what percentage of matches are won by the team that wins the toss, broken down by their toss decision (choosing to bat first or bowl first).

In [1]:
import requests

url = "https://cricbuzz-cricket.p.rapidapi.com/matches/v1/recent"

headers = {
    "x-rapidapi-key": "c3eb5c8d81mshc7823828f04b3e9p1dd037jsnf4bc6d347d8d",
    "x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}

response = requests.get(url, headers=headers)
data = response.json()
print(data)

{'typeMatches': [{'matchType': 'International', 'seriesMatches': [{'seriesAdWrapper': {'seriesId': 9107, 'seriesName': 'The Ashes, 2025-26', 'matches': [{'matchInfo': {'matchId': 108811, 'seriesId': 9107, 'seriesName': 'The Ashes, 2025-26', 'matchDesc': '5th Test', 'matchFormat': 'TEST', 'startDate': '1767483000000', 'endDate': '1767853800000', 'state': 'Complete', 'status': 'Australia won by 5 wkts', 'team1': {'teamId': 9, 'teamName': 'England', 'teamSName': 'ENG', 'imageId': 776237}, 'team2': {'teamId': 4, 'teamName': 'Australia', 'teamSName': 'AUS', 'imageId': 776202}, 'venueInfo': {'id': 34, 'ground': 'Sydney Cricket Ground', 'city': 'Sydney', 'timezone': '+11:00', 'latitude': '-33.868820', 'longitude': '151.209296'}, 'currBatTeamId': 4, 'seriesStartDt': '1763683200000', 'seriesEndDt': '1768003200000', 'isTimeAnnounced': True, 'stateTitle': 'AUS Won'}, 'matchScore': {'team1Score': {'inngs1': {'inningsId': 1, 'runs': 384, 'wickets': 10, 'overs': 97.3}, 'inngs2': {'inningsId': 3, 'ru

In [ ]:
import requests

RAPIDAPI_HOST = "cricbuzz-cricket.p.rapidapi.com"
RAPIDAPI_KEY  = "c3eb5c8d81mshc7823828f04b3e9p1dd037jsnf4bc6d347d8d"

headers = {
    "X-RapidAPI-Key": RAPIDAPI_KEY,
    "X-RapidAPI-Host": RAPIDAPI_HOST
}

records = []
MAX_RECORDS = 30

for type_match in data.get("typeMatches", []):
    for series in type_match.get("seriesMatches", []):
        matches = series.get("seriesAdWrapper", {}).get("matches", [])
        for wrapper in matches:

            if len(records) >= MAX_RECORDS:
                break

            match_info = wrapper.get("matchInfo", {})

            match_id = match_info.get("matchId")
            team1 = match_info.get("team1", {}).get("teamName")
            team2 = match_info.get("team2", {}).get("teamName")

            if not match_id:
                continue

            full_url = f"https://cricbuzz-cricket.p.rapidapi.com/mcenter/v1/{match_id}/scard"
            full_resp = requests.get(full_url, headers=headers).json()

            header = full_resp.get("matchHeader", {})
            toss_results = header.get("tossResults", {})
            result = header.get("result", {})

            records.append({
                "match_id": match_id,
                "team1": team1,
                "team2": team2,
                "toss_winner_id": toss_results.get("tossWinnerId"),
                "toss_decision": toss_results.get("decision"), 
                "toss_winner_name": toss_results.get("tossWinnerName"),
                "match_winner": result.get("winningTeam")
            })

        if len(records) >= MAX_RECORDS:
            break
    if len(records) >= MAX_RECORDS:
        break

print(records)


[{'match_id': 108811, 'team1': 'England', 'team2': 'Australia', 'toss_winner_id': None, 'toss_decision': None, 'toss_winner_name': None, 'match_winner': None}, {'match_id': 140171, 'team1': 'Sri Lanka', 'team2': 'Pakistan', 'toss_winner_id': None, 'toss_decision': None, 'toss_winner_name': None, 'match_winner': None}, {'match_id': 140160, 'team1': 'Sri Lanka', 'team2': 'Pakistan', 'toss_winner_id': None, 'toss_decision': None, 'toss_winner_name': None, 'match_winner': None}, {'match_id': 126515, 'team1': 'Durbans Super Giants', 'team2': 'Sunrisers Eastern Cape', 'toss_winner_id': None, 'toss_decision': None, 'toss_winner_name': None, 'match_winner': None}, {'match_id': 126460, 'team1': 'Pretoria Capitals', 'team2': 'Durbans Super Giants', 'toss_winner_id': None, 'toss_decision': None, 'toss_winner_name': None, 'match_winner': None}, {'match_id': 126521, 'team1': 'Pretoria Capitals', 'team2': 'Paarl Royals', 'toss_winner_id': None, 'toss_decision': None, 'toss_winner_name': None, 'match

In [ ]:
import psycopg2

conn = psycopg2.connect(
    host="localhost",
    port="5432",
    dbname="Cricbuzz",
    user="postgres",
    password="Tanvikha@1998"
)

cursor = conn.cursor()
print("DB connected")

insert_query = """
INSERT INTO win_pecentage_17
(match_id, toss_winner, toss_decision, match_winner)
VALUES (%s, %s, %s, %s)
"""
for r in records:
    cursor.execute(
        insert_query,
        (
            r["match_id"],
            r["toss_winner_name"],
            r["toss_decision"],
            r["match_winner"]
        )
    )

conn.commit()
cursor.close()
conn.close()

print("Values added successfully")


DB connected
Values added successfully


Question 18 Find the most economical bowlers in limited-overs cricket (ODI and T20 formats). Calculate each bowler's overall economy rate and total wickets taken. Only consider bowlers who have bowled in at least 10 matches and bowled at least 2 overs per match on average.

In [1]:
import requests

url = "https://cricbuzz-cricket.p.rapidapi.com/teams/v1/2/players"

headers = {
	"x-rapidapi-key": "c3eb5c8d81mshc7823828f04b3e9p1dd037jsnf4bc6d347d8d",
	"x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}

response = requests.get(url, headers=headers)
data = response.json()
print(response.json())

{'player': [{'name': 'BATSMEN', 'imageId': 174146}, {'id': '11808', 'name': 'Shubman Gill', 'imageId': 616515, 'battingStyle': 'Right-hand bat', 'bowlingStyle': 'Right-arm offbreak'}, {'id': '13940', 'name': 'Yashasvi Jaiswal', 'imageId': 591942, 'battingStyle': 'Left-hand bat', 'bowlingStyle': 'Right-arm legbreak'}, {'id': '13866', 'name': 'Sai Sudharsan', 'imageId': 717782, 'battingStyle': 'Left-hand bat', 'bowlingStyle': 'Right-arm legbreak'}, {'id': '576', 'name': 'Rohit Sharma', 'imageId': 616514, 'battingStyle': 'Right-hand bat', 'bowlingStyle': 'Right-arm offbreak'}, {'id': '1413', 'name': 'Virat Kohli', 'imageId': 616517, 'battingStyle': 'Right-hand bat', 'bowlingStyle': 'Right-arm medium'}, {'id': '7915', 'name': 'Suryakumar Yadav', 'imageId': 352481, 'battingStyle': 'Right-hand bat', 'bowlingStyle': 'Right-arm offbreak'}, {'id': '9428', 'name': 'Shreyas Iyer', 'imageId': 616518, 'battingStyle': 'Right-hand bat', 'bowlingStyle': 'Right-arm legbreak'}, {'id': '10896', 'name': '

In [ ]:
import requests

API_KEY = "c3eb5c8d81mshc7823828f04b3e9p1dd037jsnf4bc6d347d8d"
API_HOST = "cricbuzz-cricket.p.rapidapi.com"

HEADERS = {
    "X-RapidAPI-Key": API_KEY,
    "X-RapidAPI-Host": API_HOST
}

PLAYER_MAP = {
    int(item["id"]): item["name"]
    for item in data.get("player", [])
    if "id" in item
}


def fetch_bowling_stats(player_id):
    url = f"https://cricbuzz-cricket.p.rapidapi.com/stats/v1/player/{player_id}/bowling"
    response = requests.get(url, headers=HEADERS)
    response.raise_for_status()
    return response.json()


def process_player(player_id, player_name):
    stats_data = fetch_bowling_stats(player_id)

    headers = stats_data.get("headers", [])
    values = stats_data.get("values", [])

    try:
        odi_idx = headers.index("ODI")
        t20_idx = headers.index("T20")
    except ValueError:
        return None

    stats = {
        row["values"][0]: row["values"]
        for row in values
    }

    matches = int(stats["Matches"][odi_idx]) + int(stats["Matches"][t20_idx])
    balls = int(stats["Balls"][odi_idx]) + int(stats["Balls"][t20_idx])
    runs = int(stats["Runs"][odi_idx]) + int(stats["Runs"][t20_idx])
    wickets = int(stats["Wickets"][odi_idx]) + int(stats["Wickets"][t20_idx])

    if matches < 10 or balls == 0:
        return None

    overs = balls / 6
    if (overs / matches) < 2:
        return None

    economy = round(runs / overs, 2)

    return {
        "player_id": player_id,
        "player_name": player_name,
        "matches": matches,
        "overs": round(overs, 1),
        "wickets": wickets,
        "economy": economy
    }

player_list = []

for pid, pname in PLAYER_MAP.items():
    try:
        record = process_player(pid, pname)
        if record:
            player_list.append(record)
    except Exception:
        continue

for p in player_list:
    print(p)


{'player_id': 9647, 'player_name': 'Hardik Pandya', 'matches': 218, 'overs': 904.5, 'wickets': 192, 'economy': 6.58}
{'player_id': 587, 'player_name': 'Ravindra Jadeja', 'matches': 281, 'overs': 1937.0, 'wickets': 286, 'economy': 5.14}
{'player_id': 8683, 'player_name': 'Shardul Thakur', 'matches': 72, 'overs': 407.7, 'wickets': 98, 'economy': 6.83}
{'player_id': 10945, 'player_name': 'Washington Sundar', 'matches': 86, 'overs': 331.8, 'wickets': 80, 'economy': 5.94}
{'player_id': 8808, 'player_name': 'Axar Patel', 'matches': 156, 'overs': 796.0, 'wickets': 157, 'economy': 5.35}
{'player_id': 10808, 'player_name': 'Mohammed Siraj', 'matches': 63, 'overs': 406.2, 'wickets': 87, 'economy': 5.55}
{'player_id': 9311, 'player_name': 'Jasprit Bumrah', 'matches': 172, 'overs': 1056.0, 'wickets': 252, 'economy': 5.1}
{'player_id': 10551, 'player_name': 'Prasidh Krishna', 'matches': 26, 'overs': 184.8, 'wickets': 45, 'economy': 6.56}
{'player_id': 8292, 'player_name': 'Kuldeep Yadav', 'matches'

In [ ]:
import psycopg2

conn = psycopg2.connect(
    host="localhost",
    port="5432",
    dbname="Cricbuzz",
    user="postgres",
    password="Tanvikha@1998"
)

cursor = conn.cursor()
print("DB connected")

for p in player_list:
    cursor.execute("""
        INSERT INTO impact_bowlers_18 (player_id, player_name, matches, overs, wickets, economy)
        VALUES (%s, %s, %s, %s, %s, %s)
        ON CONFLICT (player_id) DO UPDATE
        SET
            matches = EXCLUDED.matches,
            overs = EXCLUDED.overs,
            wickets = EXCLUDED.wickets,
            economy = EXCLUDED.economy;
    """, (p['player_id'], p['player_name'], p['matches'], p['overs'], p['wickets'], p['economy']))

conn.commit()
cursor.close()
conn.close()

print("Values added successfully")


DB connected
Values added successfully


Question 19 Determine which batsmen are most consistent in their scoring. Calculate the average runs scored and the standard deviation of runs for each player. Only include players who have faced at least 10 balls per innings and played since 2022. A lower standard deviation indicates more consistent performance.


In [1]:
import requests

url = "https://cricbuzz-cricket.p.rapidapi.com/teams/v1/2/players"

headers = {
	"x-rapidapi-key": "c3eb5c8d81mshc7823828f04b3e9p1dd037jsnf4bc6d347d8d",
	"x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}

response = requests.get(url, headers=headers)
data = response.json()
print(response.json())

{'player': [{'name': 'BATSMEN', 'imageId': 174146}, {'id': '11808', 'name': 'Shubman Gill', 'imageId': 616515, 'battingStyle': 'Right-hand bat', 'bowlingStyle': 'Right-arm offbreak'}, {'id': '13940', 'name': 'Yashasvi Jaiswal', 'imageId': 591942, 'battingStyle': 'Left-hand bat', 'bowlingStyle': 'Right-arm legbreak'}, {'id': '13866', 'name': 'Sai Sudharsan', 'imageId': 717782, 'battingStyle': 'Left-hand bat', 'bowlingStyle': 'Right-arm legbreak'}, {'id': '576', 'name': 'Rohit Sharma', 'imageId': 616514, 'battingStyle': 'Right-hand bat', 'bowlingStyle': 'Right-arm offbreak'}, {'id': '1413', 'name': 'Virat Kohli', 'imageId': 616517, 'battingStyle': 'Right-hand bat', 'bowlingStyle': 'Right-arm medium'}, {'id': '7915', 'name': 'Suryakumar Yadav', 'imageId': 352481, 'battingStyle': 'Right-hand bat', 'bowlingStyle': 'Right-arm offbreak'}, {'id': '9428', 'name': 'Shreyas Iyer', 'imageId': 616518, 'battingStyle': 'Right-hand bat', 'bowlingStyle': 'Right-arm legbreak'}, {'id': '10896', 'name': '

In [ ]:
import requests

API_KEY = "c3eb5c8d81mshc7823828f04b3e9p1dd037jsnf4bc6d347d8d"
BASE_URL = "https://cricbuzz-cricket.p.rapidapi.com"

headers = {
    "X-RapidAPI-Key": API_KEY,
    "X-RapidAPI-Host": "cricbuzz-cricket.p.rapidapi.com"
}
PLAYER_MAP = {
    int(item["id"]): item["name"]
    for item in data.get("player", [])
    if "id" in item
}

def fetch_batting_stats(player_id):
    url = f"{BASE_URL}/stats/v1/player/{player_id}/batting"
    response = requests.get(url, headers=headers)
    return response.json()

def parse_batting_response(data, player_name):
    headers_row = data["headers"][1:] 
    values = data["values"]

    stats = {}
    for row in values:
        key = row["values"][0]
        stats[key] = row["values"][1:]

    result = []

    for idx, format_name in enumerate(headers_row):
        innings = int(stats["Innings"][idx])
        runs = int(stats["Runs"][idx])
        balls = int(stats["Balls"][idx])

        if innings > 0 and (balls / innings) >= 10:
            avg_runs = round(runs / innings, 2)

            result.append({
                "player": player_name,
                "format": format_name,
                "innings": innings,
                "total_runs": runs,
                "average_runs": avg_runs,
                "std_deviation": None
            })

    return result


final_result = []

for pid, pname in PLAYER_MAP.items():
    data = fetch_batting_stats(pid)
    parsed = parse_batting_response(data, pname)
    final_result.extend(parsed)

print(final_result)


[{'player': 'Shubman Gill', 'format': 'Test', 'innings': 73, 'total_runs': 2843, 'average_runs': 38.95, 'std_deviation': None, 'note': 'Std deviation requires innings-level scores'}, {'player': 'Shubman Gill', 'format': 'ODI', 'innings': 59, 'total_runs': 2874, 'average_runs': 48.71, 'std_deviation': None, 'note': 'Std deviation requires innings-level scores'}, {'player': 'Shubman Gill', 'format': 'T20', 'innings': 36, 'total_runs': 869, 'average_runs': 24.14, 'std_deviation': None, 'note': 'Std deviation requires innings-level scores'}, {'player': 'Shubman Gill', 'format': 'IPL', 'innings': 115, 'total_runs': 3866, 'average_runs': 33.62, 'std_deviation': None, 'note': 'Std deviation requires innings-level scores'}, {'player': 'Yashasvi Jaiswal', 'format': 'Test', 'innings': 53, 'total_runs': 2511, 'average_runs': 47.38, 'std_deviation': None, 'note': 'Std deviation requires innings-level scores'}, {'player': 'Yashasvi Jaiswal', 'format': 'ODI', 'innings': 4, 'total_runs': 171, 'averag

In [ ]:
import psycopg2

conn = psycopg2.connect(
    host="localhost",
    port="5432",
    dbname="Cricbuzz",
    user="postgres",
    password="Tanvikha@1998"
)

cursor = conn.cursor()
print("DB connected")

insert_query = """
INSERT INTO batting_consistency_19
(player_name, format, innings, total_runs, average_runs, std_deviation, note)
VALUES (%s, %s, %s, %s, %s, %s, %s)
"""

for r in final_result:
    cursor.execute(
        insert_query,
        (
            r["player"],
            r["format"],
            r["innings"],
            r["total_runs"],
            r["average_runs"],
            r["std_deviation"],  
            r["note"]
        )
    )

conn.commit()
cursor.close()
conn.close()

print("Batting consistency values added successfully")


DB connected
Batting consistency values added successfully


Question 20 Analyze how many matches each player has played in different cricket formats and their batting average in each format. Show the count of Test matches, ODI matches, and T20 matches for each player, along with their respective batting averages. Only include players who have played at least 20 total matches across all formats.

In [ ]:
import requests

API_KEY = "c3eb5c8d81mshc7823828f04b3e9p1dd037jsnf4bc6d347d8d"
BASE_URL = "https://cricbuzz-cricket.p.rapidapi.com"

headers = {
    "X-RapidAPI-Key": API_KEY,
    "X-RapidAPI-Host": "cricbuzz-cricket.p.rapidapi.com"
}
PLAYER_MAP = {
    int(item["id"]): item["name"]
    for item in data.get("player", [])
    if "id" in item
}

def fetch_player_stats(player_id):
    url = f"{BASE_URL}/stats/v1/player/{player_id}/batting"
    response = requests.get(url, headers=headers)
    return response.json()

def parse_player_stats(data, player_name):
    formats = data["headers"][1:] 

    stats = {}
    for row in data["values"]:
        key = row["values"][0]
        stats[key] = row["values"][1:]

    result = {
        "player": player_name,
        "test_matches": 0,
        "test_avg": None,
        "odi_matches": 0,
        "odi_avg": None,
        "t20_matches": 0,
        "t20_avg": None,
        "total_matches": 0
    }

    for i, fmt in enumerate(formats):
        matches = int(stats.get("Matches", ["0"] * 4)[i])
        avg = stats.get("Avg", [None] * 4)[i]

        if fmt == "Test":
            result["test_matches"] = matches
            result["test_avg"] = float(avg) if avg not in ["-", None] else None
        elif fmt == "ODI":
            result["odi_matches"] = matches
            result["odi_avg"] = float(avg) if avg not in ["-", None] else None
        elif fmt == "T20":
            result["t20_matches"] = matches
            result["t20_avg"] = float(avg) if avg not in ["-", None] else None

        if fmt in ["Test", "ODI", "T20"]:
            result["total_matches"] += matches

    return result
final_result = []

for pid, pname in PLAYER_MAP.items():
    data = fetch_player_stats(pid)
    player_summary = parse_player_stats(data, pname)


    if player_summary["total_matches"] >= 20:
        final_result.append(player_summary)

print(final_result)

Question 21 Create a comprehensive performance ranking system for players. Combine their batting performance (runs scored, batting average, strike rate), bowling performance (wickets taken, bowling average, economy rate), and fielding performance (catches, stumpings, Run out) into a single weighted score. Use this formula and rank players:
Batting points: (runs_scored × 0.01) + (batting_average × 0.5) + (strike_rate × 0.3)
Bowling points: (wickets_taken × 2) + (50 - bowling_average) × 0.5) + ((6 - economy_rate) × 2)

In [ ]:
import requests

API_KEY = "c3eb5c8d81mshc7823828f04b3e9p1dd037jsnf4bc6d347d8d"
HOST = "cricbuzz-cricket.p.rapidapi.com"

HEADERS = {
    "x-rapidapi-key": API_KEY,
    "x-rapidapi-host": HOST
}

PLAYER_IDS = [
    11808,13940,13866,576,1413,7915,9428,10896,14504,11813,
    10636,9429,9716,8257,11195,12086,587,10945,8808,10744,
    8733,14691,8271,10276,10808,9311,10551,8292,13217,14659,12926
]

FORMATS = ["Test", "ODI", "T20", "IPL"]

def extract_stat(response, stat_name):
    for row in response.get("values", []):
        if row["values"][0] == stat_name:
            return [float(x) if x not in ("-", "") else 0 for x in row["values"][1:]]
    return [0] * 4


results = []


for player_id in PLAYER_IDS:

    BAT_URL = f"https://cricbuzz-cricket.p.rapidapi.com/stats/v1/player/{player_id}/batting"
    BOWL_URL = f"https://cricbuzz-cricket.p.rapidapi.com/stats/v1/player/{player_id}/bowling"

    batting_response = requests.get(BAT_URL, headers=HEADERS).json()
    bowling_response = requests.get(BOWL_URL, headers=HEADERS).json()

   
    runs = extract_stat(batting_response, "Runs")
    bat_avg = extract_stat(batting_response, "Average")
    strike_rate = extract_stat(batting_response, "SR")

   
    wickets = extract_stat(bowling_response, "Wickets")
    bowl_avg = extract_stat(bowling_response, "Avg")
    economy = extract_stat(bowling_response, "Eco")

    for i, fmt in enumerate(FORMATS):

        batting_points = (
            runs[i] * 0.01 +
            bat_avg[i] * 0.5 +
            strike_rate[i] * 0.3
        )

        if wickets[i] == 0:
            bowling_points = 0
        else:
            bowling_points = (
                wickets[i] * 2 +
                (50 - bowl_avg[i]) * 0.5 +
                (6 - economy[i]) * 2
            )

        total_score = batting_points + bowling_points

        results.append({
            "player_id": player_id,
            "format": fmt,
            "batting_points": round(batting_points, 2),
            "bowling_points": round(bowling_points, 2),
            "total_score": round(total_score, 2)
        })
print(results)


[{'player_id': 11808, 'format': 'Test', 'batting_points': 0.0, 'bowling_points': 0, 'total_score': 0.0}, {'player_id': 11808, 'format': 'ODI', 'batting_points': 0.0, 'bowling_points': 0, 'total_score': 0.0}, {'player_id': 11808, 'format': 'T20', 'batting_points': 0.0, 'bowling_points': 0, 'total_score': 0.0}, {'player_id': 11808, 'format': 'IPL', 'batting_points': 0.0, 'bowling_points': 0, 'total_score': 0.0}, {'player_id': 13940, 'format': 'Test', 'batting_points': 0.0, 'bowling_points': 0, 'total_score': 0.0}, {'player_id': 13940, 'format': 'ODI', 'batting_points': 0.0, 'bowling_points': 0, 'total_score': 0.0}, {'player_id': 13940, 'format': 'T20', 'batting_points': 0.0, 'bowling_points': 0, 'total_score': 0.0}, {'player_id': 13940, 'format': 'IPL', 'batting_points': 0.0, 'bowling_points': 0, 'total_score': 0.0}, {'player_id': 13866, 'format': 'Test', 'batting_points': 0.0, 'bowling_points': 0, 'total_score': 0.0}, {'player_id': 13866, 'format': 'ODI', 'batting_points': 0.0, 'bowling

In [ ]:
import psycopg2
conn = psycopg2.connect(
    host="localhost",
    port="5432",
    dbname="Cricbuzz",
    user="postgres",
    password="Tanvikha@1998"
)

cursor = conn.cursor()
print("DB connected")

insert_query = """
INSERT INTO player_performance_21
(player_id, format, batting_points, bowling_points, total_score)
VALUES (%s, %s, %s, %s, %s)
"""

for r in results:
    cursor.execute(
        insert_query,
        (
            r["player_id"],
            r["format"],
            r["batting_points"],
            r["bowling_points"],
            r["total_score"]
        )
    )

conn.commit()
cursor.close()
conn.close()

print("Player performance values added successfully ")


DB connected
Player performance values added successfully ✅


Question 22 Build a head-to-head match prediction analysis between teams. For each pair of teams that have played at least 5 matches against each other in the last 3 years, calculate:
Total matches played between them
Wins for each team
Average victory margin when each team wins
Performance when batting first vs bowling first at different venues
Overall win percentage for each team in this head-to-head record

In [6]:
import requests

url = "https://cricbuzz-cricket.p.rapidapi.com/matches/v1/recent"

headers = {
	"x-rapidapi-key": "ecfbe010eamshe6896ce1cba10b1p1c0f57jsn0a2a56b140e5",
	"x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}

response = requests.get(url, headers=headers)
matchIdRes = response.json()
print(response.json())


{'typeMatches': [{'matchType': 'International', 'seriesMatches': [{'seriesAdWrapper': {'seriesId': 10102, 'seriesName': 'New Zealand tour of India, 2026', 'matches': [{'matchInfo': {'matchId': 121400, 'seriesId': 10102, 'seriesName': 'New Zealand tour of India, 2026', 'matchDesc': '2nd T20I', 'matchFormat': 'T20', 'startDate': '1769175000000', 'endDate': '1769187600000', 'state': 'Complete', 'status': 'India won by 7 wkts', 'team1': {'teamId': 13, 'teamName': 'New Zealand', 'teamSName': 'NZ', 'imageId': 776333}, 'team2': {'teamId': 2, 'teamName': 'India', 'teamSName': 'IND', 'imageId': 776162}, 'venueInfo': {'id': 335, 'ground': 'Shaheed Veer Narayan Singh International Stadium', 'city': 'Raipur', 'timezone': '+05:30', 'latitude': '21.203523', 'longitude': '81.823929'}, 'currBatTeamId': 2, 'seriesStartDt': '1768089600000', 'seriesEndDt': '1769990400000', 'isTimeAnnounced': True, 'stateTitle': 'IND Won', 'isFantasyEnabled': True}, 'matchScore': {'team1Score': {'inngs1': {'inningsId': 1,

In [7]:
matchIdRes

{'typeMatches': [{'matchType': 'International',
   'seriesMatches': [{'seriesAdWrapper': {'seriesId': 10102,
      'seriesName': 'New Zealand tour of India, 2026',
      'matches': [{'matchInfo': {'matchId': 121400,
         'seriesId': 10102,
         'seriesName': 'New Zealand tour of India, 2026',
         'matchDesc': '2nd T20I',
         'matchFormat': 'T20',
         'startDate': '1769175000000',
         'endDate': '1769187600000',
         'state': 'Complete',
         'status': 'India won by 7 wkts',
         'team1': {'teamId': 13,
          'teamName': 'New Zealand',
          'teamSName': 'NZ',
          'imageId': 776333},
         'team2': {'teamId': 2,
          'teamName': 'India',
          'teamSName': 'IND',
          'imageId': 776162},
         'venueInfo': {'id': 335,
          'ground': 'Shaheed Veer Narayan Singh International Stadium',
          'city': 'Raipur',
          'timezone': '+05:30',
          'latitude': '21.203523',
          'longitude': '81.82392

In [ ]:
import requests
from datetime import datetime, timedelta
from collections import defaultdict
import re
import psycopg2
import json
RAPIDAPI_KEY = "ecfbe010eamshe6896ce1cba10b1p1c0f57jsn0a2a56b140e5" 
API_HOST = "cricbuzz-cricket.p.rapidapi.com"
SCORECARD_URL = "https://cricbuzz-cricket.p.rapidapi.com/mcenter/v1/{match_id}/scard"

HEADERS = {
    "X-RapidAPI-Key": RAPIDAPI_KEY,
    "X-RapidAPI-Host": API_HOST
}

def extract_match_ids(api_response):
    match_ids = []
    for type_match in api_response.get("typeMatches", []):
        for series in type_match.get("seriesMatches", []):
            for match in series.get("seriesAdWrapper", {}).get("matches", []):
                match_id = match.get("matchInfo", {}).get("matchId")
                if match_id:
                    match_ids.append(match_id)
    return match_ids

def fetch_scorecard(match_id):
    url = SCORECARD_URL.format(match_id=match_id)
    response = requests.get(url, headers=HEADERS, timeout=20)
    response.raise_for_status()
    return response.json()

def parse_match(scorecard, match_id):
    header = scorecard.get("matchHeader", {})
    teams = header.get("teamDetails", {})

    team1 = teams.get("team1", {}).get("name")
    team2 = teams.get("team2", {}).get("name")

    result = header.get("result", {})
    winner = result.get("winningTeam")
    margin = result.get("winningMargin") 

    toss = header.get("tossResults", {})
    toss_winner = toss.get("tossWinnerName")
    toss_decision = toss.get("decision") 

    venue_info = header.get("groundDetails", {})
    venue = venue_info.get("groundName")

    match_date = header.get("matchStartTimestamp")
    if match_date:
        match_date = datetime.fromtimestamp(int(match_date)/1000)

    return {
        "match_id": match_id,
        "team1": team1,
        "team2": team2,
        "winner": winner,
        "margin": margin,
        "toss_winner": toss_winner,
        "toss_decision": toss_decision,
        "venue": venue,
        "match_date": match_date
    }


def build_match_list(matchIdRes):
    records = []
    match_ids = extract_match_ids(matchIdRes)
    for match_id in match_ids:
        try:
            scorecard = fetch_scorecard(match_id)
            records.append(parse_match(scorecard, match_id))
        except Exception as e:
            print(f"Error processing match {match_id}: {e}")
    return records


def extract_margin_value(margin):
    if not margin:
        return None
    num = re.findall(r"\d+", margin)
    return int(num[0]) if num else None


def head_to_head_analysis(matches):
    three_years_ago = datetime.now() - timedelta(days=3*365)
    h2h = defaultdict(list)

  
    for m in matches:
        if not m["match_date"] or m["match_date"] < three_years_ago:
            continue
        if not m["team1"] or not m["team2"] or not m["winner"]:
            continue
        pair = " vs ".join(sorted([m["team1"], m["team2"]]))
        h2h[pair].append(m)

    results = []

    for pair, games in h2h.items():
        if len(games) < 5:
            continue

        team_a, team_b = pair.split(" vs ")

        total_matches = len(games)
        wins_a = wins_b = 0
        margin_a = []
        margin_b = []
        bat_first_a = bowl_first_a = 0
        bat_first_b = bowl_first_b = 0
        venue_stats = defaultdict(int)

        for g in games:
            margin_val = extract_margin_value(g["margin"])

           
            if g["winner"] == team_a:
                wins_a += 1
                if margin_val:
                    margin_a.append(margin_val)
            elif g["winner"] == team_b:
                wins_b += 1
                if margin_val:
                    margin_b.append(margin_val)

          
            if g["toss_winner"] and g["toss_decision"]:
                if g["toss_decision"] == "bat":
                    batting_first = g["toss_winner"]
                else:
                    batting_first = team_b if g["toss_winner"] == team_a else team_a

                if g["winner"] == team_a:
                    if batting_first == team_a:
                        bat_first_a += 1
                    else:
                        bowl_first_a += 1
                if g["winner"] == team_b:
                    if batting_first == team_b:
                        bat_first_b += 1
                    else:
                        bowl_first_b += 1

            
            if g["venue"]:
                venue_stats[g["venue"]] += 1

        results.append({
            "team_a": team_a,
            "team_b": team_b,
            "total_matches": total_matches,
            "team_a_wins": wins_a,
            "team_b_wins": wins_b,
            "team_a_win_pct": round(wins_a/total_matches*100,2),
            "team_b_win_pct": round(wins_b/total_matches*100,2),
            "avg_margin_team_a": round(sum(margin_a)/len(margin_a),2) if margin_a else None,
            "avg_margin_team_b": round(sum(margin_b)/len(margin_b),2) if margin_b else None,
            "batting_first_wins_team_a": bat_first_a,
            "bowling_first_wins_team_a": bowl_first_a,
            "batting_first_wins_team_b": bat_first_b,
            "bowling_first_wins_team_b": bowl_first_b,
            "venue_summary": dict(venue_stats),
            "analysis_period_years": 3
        })

    return results


def insert_h2h_into_db(results):
    conn = psycopg2.connect(
        host="localhost",
        port="5432",
        dbname="Cricbuzz",
        user="postgres",
        password="Tanvikha@1998"
    )
    cursor = conn.cursor()
    print("DB connected")

    insert_query = """
    INSERT INTO head_to_head_analysis (
        team_a,
        team_b,
        total_matches,
        team_a_wins,
        team_b_wins,
        team_a_win_percentage,
        team_b_win_percentage,
        avg_margin_team_a,
        avg_margin_team_b,
        batting_first_wins_team_a,
        bowling_first_wins_team_a,
        batting_first_wins_team_b,
        bowling_first_wins_team_b,
        venue,
        analysis_period_years
    )
    VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s)
    """

    for r in results:
        cursor.execute(
            insert_query,
            (
                r["team_a"],
                r["team_b"],
                r["total_matches"],
                r["team_a_wins"],
                r["team_b_wins"],
                r["team_a_win_pct"],
                r["team_b_win_pct"],
                r["avg_margin_team_a"],
                r["avg_margin_team_b"],
                r["batting_first_wins_team_a"],
                r["bowling_first_wins_team_a"],
                r["batting_first_wins_team_b"],
                r["bowling_first_wins_team_b"],
                json.dumps(r["venue_summary"]), 
                r["analysis_period_years"]
            )
        )

    conn.commit()
    cursor.close()
    conn.close()
    print("Head-to-head analysis data inserted successfully ")

if __name__ == "__main__":
    df_matches = build_match_list(matchIdRes)
    results = head_to_head_analysis(df_matches)

    print("\nQUESTION 22 – HEAD TO HEAD ANALYSIS\n")
    print(json.dumps(results, indent=2))

  
    insert_h2h_into_db(results)


In [16]:
results

[]

In [ ]:
import psycopg2


conn = psycopg2.connect(
    host="localhost",
    port="5432",
    dbname="Cricbuzz",
    user="postgres",
    password="Tanvikha@1998"
)

cursor = conn.cursor()
print("DB connected")

insert_query = """
INSERT INTO head_to_head_analysis (
    team_a,
    team_b,
    total_matches,
    team_a_wins,
    team_b_wins,
    team_a_win_percentage,
    team_b_win_percentage,
    avg_margin_team_a,
    avg_margin_team_b,
    batting_first_wins_team_a,
    bowling_first_wins_team_a,
    batting_first_wins_team_b,
    bowling_first_wins_team_b,
    venue,
    analysis_period_years
)
VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s)
"""

for r in results:
    cursor.execute(
        insert_query,
        (
            r["team_a"],
            r["team_b"],
            r["total_matches"],
            r["team_a_wins"],
            r["team_b_wins"],
            r["team_a_win_pct"],
            r["team_b_win_pct"],
            r["avg_margin_team_a"],
            r["avg_margin_team_b"],
            r["batting_first_wins_team_a"],
            r["bowling_first_wins_team_a"],
            r["batting_first_wins_team_b"],
            r["bowling_first_wins_team_b"],
            r["venue"],
            3  
        )
    )
conn.commit()
cursor.close()
conn.close()

print("Head-to-head analysis data inserted successfully ")


Question 23 Analyze recent player form and momentum. For each player's last 10 batting performances, calculate:
Average runs in their last 5 matches vs their last 10 matches
Recent strike rate trends
Number of scores above 50 in recent matches
A consistency score based on standard deviation
Based on these metrics, categorize players as being in "Excellent Form", "Good Form", "Average Form", or "Poor Form".

In [12]:
import requests

url = "https://cricbuzz-cricket.p.rapidapi.com/matches/v1/recent"

headers = {
	"x-rapidapi-key": "a958600c89msh2a8c6e7d121682dp14711ejsn2bbc4ce6bead",
	"x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}

response = requests.get(url, headers=headers)
data = response.json()
print(response.json())

{'typeMatches': [{'matchType': 'International', 'seriesMatches': [{'seriesAdWrapper': {'seriesId': 10102, 'seriesName': 'New Zealand tour of India, 2026', 'matches': [{'matchInfo': {'matchId': 121406, 'seriesId': 10102, 'seriesName': 'New Zealand tour of India, 2026', 'matchDesc': '3rd T20I', 'matchFormat': 'T20', 'startDate': '1769347800000', 'endDate': '1769360400000', 'state': 'Complete', 'status': 'India won by 8 wkts', 'team1': {'teamId': 13, 'teamName': 'New Zealand', 'teamSName': 'NZ', 'imageId': 776333}, 'team2': {'teamId': 2, 'teamName': 'India', 'teamSName': 'IND', 'imageId': 776162}, 'venueInfo': {'id': 380, 'ground': 'Barsapara Cricket Stadium', 'city': 'Guwahati', 'timezone': '+05:30', 'latitude': '26.094292', 'longitude': '91.785187'}, 'currBatTeamId': 2, 'seriesStartDt': '1768089600000', 'seriesEndDt': '1769990400000', 'isTimeAnnounced': True, 'stateTitle': 'Complete', 'isFantasyEnabled': True}, 'matchScore': {'team1Score': {'inngs1': {'inningsId': 1, 'runs': 153, 'wicke

In [13]:
data

{'typeMatches': [{'matchType': 'International',
   'seriesMatches': [{'seriesAdWrapper': {'seriesId': 10102,
      'seriesName': 'New Zealand tour of India, 2026',
      'matches': [{'matchInfo': {'matchId': 121406,
         'seriesId': 10102,
         'seriesName': 'New Zealand tour of India, 2026',
         'matchDesc': '3rd T20I',
         'matchFormat': 'T20',
         'startDate': '1769347800000',
         'endDate': '1769360400000',
         'state': 'Complete',
         'status': 'India won by 8 wkts',
         'team1': {'teamId': 13,
          'teamName': 'New Zealand',
          'teamSName': 'NZ',
          'imageId': 776333},
         'team2': {'teamId': 2,
          'teamName': 'India',
          'teamSName': 'IND',
          'imageId': 776162},
         'venueInfo': {'id': 380,
          'ground': 'Barsapara Cricket Stadium',
          'city': 'Guwahati',
          'timezone': '+05:30',
          'latitude': '26.094292',
          'longitude': '91.785187'},
         'currBa

In [14]:
match_ids = []

for type_match in data.get("typeMatches", []):
    for series_match in type_match.get("seriesMatches", []):
        series_wrapper = series_match.get("seriesAdWrapper", {})
        for match in series_wrapper.get("matches", []):
            match_info = match.get("matchInfo", {})
            if "matchId" in match_info:
                match_ids.append({"match_id": match_info["matchId"]})

print(match_ids)

[{'match_id': 121406}, {'match_id': 121400}, {'match_id': 121389}, {'match_id': 133011}, {'match_id': 133000}, {'match_id': 140537}, {'match_id': 140548}, {'match_id': 137826}, {'match_id': 137831}, {'match_id': 137819}, {'match_id': 126653}, {'match_id': 126642}, {'match_id': 126636}, {'match_id': 126625}, {'match_id': 126620}, {'match_id': 123468}, {'match_id': 123457}, {'match_id': 123452}, {'match_id': 123441}, {'match_id': 140492}, {'match_id': 140525}, {'match_id': 140503}, {'match_id': 140514}, {'match_id': 132978}, {'match_id': 132940}, {'match_id': 132934}, {'match_id': 132962}, {'match_id': 132951}, {'match_id': 132973}, {'match_id': 132967}, {'match_id': 138535}, {'match_id': 138513}, {'match_id': 138502}, {'match_id': 138524}, {'match_id': 138458}, {'match_id': 138447}, {'match_id': 138425}, {'match_id': 138491}, {'match_id': 138414}, {'match_id': 138480}, {'match_id': 138436}, {'match_id': 138469}, {'match_id': 138515}, {'match_id': 138403}, {'match_id': 138392}, {'match_i

In [ ]:
import requests

BASE_URL = "https://cricbuzz-cricket.p.rapidapi.com/mcenter/v1/{match_id}"

headers = {
    "x-rapidapi-key": "a958600c89msh2a8c6e7d121682dp14711ejsn2bbc4ce6bead",
    "x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
}

all_players = {}

for match_id in match_ids[:20]:
    url = BASE_URL.format(match_id=match_id)
    response = requests.get(url, headers=headers)

    if response.status_code != 200:
        print(f"Failed for match {match_id}")
        continue

    data = response.json()
    match_info = data.get("matchInfo", {})
    player_ids = set()

    for player in match_info.get("team1", {}).get("playerDetails", []):
        player_ids.add(player.get("id"))

    for player in match_info.get("team2", {}).get("playerDetails", []):
        player_ids.add(player.get("id"))

    all_players[match_id] = list(player_ids)

print(all_players)


In [ ]:
import psycopg2

conn = psycopg2.connect(
    host="localhost",
    port="5432",
    dbname="Cricbuzz",
    user="postgres",
    password="Tanvikha@1998"
)

cursor = conn.cursor()
print("DB connected")

insert_query = """
INSERT INTO player_recent_form_23 (
    player_id,
    player_name,
    avg_runs_last_5,
    avg_runs_last_10,
    strike_rate_last_5,
    strike_rate_last_10,
    fifties_last_10,
    runs_std_dev,
    consistency_score,
    form_category
)
VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s)
"""

for r in player_results:
    cursor.execute(
        insert_query,
        (
            r["player_id"],
            r["player_name"],
            r["avg_runs_last_5"],
            r["avg_runs_last_10"],
            r["strike_rate_last_5"],
            r["strike_rate_last_10"],
            r["fifties_last_10"],
            r["runs_std_dev"],
            r.get("consistency_score"),
            r.get("form_category") 
        )
    )

conn.commit()
cursor.close()
conn.close()

print("Player recent form data inserted successfully")


Question 24 Study successful batting partnerships to identify the best player combinations. For pairs of players who have batted together as consecutive batsmen (positions differ by 1) in at least 5 partnerships:
Calculate their average partnership runs
Count how many of their partnerships exceeded 50 runs
Find their highest partnership score
Calculate their success rate (percentage of good partnerships)
Rank the most successful batting partnerships.

In [ ]:
import requests

detailed_matches = []

for match in all_matches:
    mid = match.get("matchId")
    city = match.get("city")
    ground = match.get("ground")
    
    url = f"https://cricbuzz-cricket.p.rapidapi.com/mcenter/v1/{mid}/scard"
    headers = {
        "x-rapidapi-key": "d63331dda4mshdc6a08299933a4fp1da5e1jsn89d940c6d2ed",
        "x-rapidapi-host": "cricbuzz-cricket.p.rapidapi.com"
    }

    response = requests.get(url, headers=headers)
    if response.status_code == 200:
        scorecard = response.json()
        scorecard["city"] = city     
        scorecard["ground"] = ground  
        detailed_matches.append(scorecard)
    else:
        print(f"Failed to fetch match {mid}: {response.status_code}")

print(f"Fetched detailed scorecards for {len(detailed_matches)} matches ")


Fetched detailed scorecards for 196 matches ✅


In [ ]:
print(detailed_matches)

[{'scorecard': [{'inningsid': 1,
    'batsman': [{'id': 11290,
      'balls': 1,
      'runs': 0,
      'fours': 0,
      'sixes': 0,
      'strkrate': '0',
      'name': 'Kushal Bhurtel',
      'nickname': '',
      'iscaptain': False,
      'iskeeper': False,
      'outdec': 'c Smit b Trumpelmann',
      'videotype': '',
      'videourl': '',
      'videoid': 0,
      'planid': 0,
      'imageid': 0,
      'premiumvideourl': '',
      'iscbplusfree': False,
      'ispremiumfree': False,
      'inmatchchange': '',
      'isoverseas': False,
      'playingxichange': ''},
     {'id': 12110,
      'balls': 11,
      'runs': 4,
      'fours': 1,
      'sixes': 0,
      'strkrate': '36.36',
      'name': 'Aasif Sheikh',
      'nickname': '',
      'iscaptain': False,
      'iskeeper': True,
      'outdec': 'c Smit b Jack Brassell',
      'videotype': '',
      'videourl': '',
      'videoid': 0,
      'planid': 0,
      'imageid': 0,
      'premiumvideourl': '',
      'iscbplusfree': False

In [ ]:
import psycopg2
from collections import defaultdict


conn = psycopg2.connect(
    host="localhost",
    port="5432",
    dbname="Cricbuzz",
    user="postgres",
    password="Tanvikha@1998"
)
cursor = conn.cursor()
print("DB connected")


insert_query = """
INSERT INTO batting_partnerships_13
(match_id, innings, player1, player2, partnership_runs)
VALUES (%s, %s, %s, %s, %s)
"""

partnership_data = [] 

for scorecard in detailed_matches:
    match_id = scorecard.get("matchInfo", {}).get("matchId")
    if not match_id:
        continue

    for inning in scorecard.get("innings", []):
        inning_number = inning.get("number")  # 1 or 2
        partnerships = inning.get("partnerships", [])

        for partnership in partnerships:
            player1 = partnership.get("batsmen", [None, None])[0]
            player2 = partnership.get("batsmen", [None, None])[1]
            partnership_runs = partnership.get("partnership", 0)

            if player1 and player2:
                cursor.execute(insert_query, (
                    match_id,
                    inning_number,
                    player1,
                    player2,
                    partnership_runs
                ))
                partnership_data.append({
                    "player1": player1,
                    "player2": player2,
                    "runs": partnership_runs
                })

conn.commit()
print("Partnerships inserted ")

partnership_stats = defaultdict(list)

for p in partnership_data:
    key = tuple(sorted([p["player1"], p["player2"]])) 
    partnership_stats[key].append(p["runs"])

result_list = []
for players, runs_list in partnership_stats.items():
    if len(runs_list) >= 5:
        total_partnerships = len(runs_list)
        avg_runs = sum(runs_list) / total_partnerships
        partnerships_above_50 = sum(1 for r in runs_list if r > 50)
        highest_partnership = max(runs_list)
        success_rate = round(100 * partnerships_above_50 / total_partnerships, 2)
        
        result_list.append({
            "player1": players[0],
            "player2": players[1],
            "total_partnerships": total_partnerships,
            "avg_runs": avg_runs,
            "partnerships_above_50": partnerships_above_50,
            "highest_partnership": highest_partnership,
            "success_rate": success_rate
        })

result_list.sort(key=lambda x: (-x["success_rate"], -x["avg_runs"]))

for r in result_list:
    print(f"Players: {r['player1']} & {r['player2']}, "
          f"Total Partnerships: {r['total_partnerships']}, "
          f"Avg Runs: {r['avg_runs']:.2f}, "
          f"50+ Partnerships: {r['partnerships_above_50']}, "
          f"Highest Partnership: {r['highest_partnership']}, "
          f"Success Rate: {r['success_rate']}%")

cursor.close()
conn.close()
print("Partnership analysis completed in Python")


Question 25 Perform a time-series analysis of player performance evolution. Track how each player's batting performance changes over time by:
Calculating quarterly averages for runs and strike rate
Comparing each quarter's performance to the previous quarter
Identifying whether performance is improving, declining, or stable
Determining overall career traaajectory over the last few years
Categorizing players' career phase as "Career Ascending", "Career Declining", or "Career Stable"
Only analyze players with data spanning at least 6 quarters and a minimum of 3 matches per quarter.


In [ ]:
import requests
from datetime import datetime
from collections import defaultdict

RAPIDAPI_KEY = "a958600c89msh2a8c6e7d121682dp14711ejsn2bbc4ce6bead"
BASE_URL = "https://cricbuzz-cricket.p.rapidapi.com"

HEADERS = {
    "X-RapidAPI-Key": RAPIDAPI_KEY,
    "X-RapidAPI-Host": "cricbuzz-cricket.p.rapidapi.com"
}


batting_data = []         
quarterly_summary = []    
career_summary = []       

matches_resp = requests.get(
    f"{BASE_URL}/matches/v1/recent",
    headers=HEADERS
).json()


for match_type in matches_resp.get("typeMatches", []):
    for series in match_type.get("seriesMatches", []):
        for match in series.get("seriesAdWrapper", {}).get("matches", []):

            match_info = match.get("matchInfo", {})
            match_id = match_info.get("matchId")
            start_date = match_info.get("startDate")

            if not match_id or not start_date:
                continue

            match_date = datetime.fromtimestamp(start_date / 1000)

            scard_resp = requests.get(
                f"{BASE_URL}/mcenter/v1/{match_id}/scard",
                headers=HEADERS
            )

            if scard_resp.status_code != 200:
                continue

            scard = scard_resp.json()

            for innings in scard.get("scoreCard", []):
                batsmen = innings.get("batTeamDetails", {}).get("batsmenData", {})
                for batter in batsmen.values():
                    balls = batter.get("balls", 0)
                    if balls == 0:
                        continue

                    runs = batter.get("runs", 0)
                    batting_data.append({
                        "player": batter.get("batName"),
                        "runs": runs,
                        "balls": balls,
                        "strike_rate": (runs / balls) * 100,
                        "quarter": f"{match_date.year}-Q{((match_date.month - 1) // 3) + 1}"
                    })
quarterly_bucket = defaultdict(lambda: defaultdict(list))

for r in batting_data:
    key = (r["player"], r["quarter"])
    quarterly_bucket[key]["runs"].append(r["runs"])
    quarterly_bucket[key]["sr"].append(r["strike_rate"])

for (player, quarter), stats in quarterly_bucket.items():
    matches = len(stats["runs"])
    if matches >= 3:
        quarterly_summary.append({
            "player": player,
            "quarter": quarter,
            "matches": matches,
            "avg_runs": sum(stats["runs"]) / matches,
            "avg_strike_rate": sum(stats["sr"]) / matches
        })

player_quarters = defaultdict(set)

for q in quarterly_summary:
    player_quarters[q["player"]].add(q["quarter"])

eligible_players = {
    p for p, qs in player_quarters.items() if len(qs) >= 6
}

quarterly_summary = [
    q for q in quarterly_summary if q["player"] in eligible_players
]


quarterly_summary.sort(key=lambda x: (x["player"], x["quarter"]))

prev = {}

for q in quarterly_summary:
    player = q["player"]

    if player in prev:
        q["runs_change"] = q["avg_runs"] - prev[player]["avg_runs"]
        q["sr_change"] = q["avg_strike_rate"] - prev[player]["avg_strike_rate"]
    else:
        q["runs_change"] = None
        q["sr_change"] = None

    prev[player] = q


def quarter_trend(r, s, threshold=0.05):
    if r is None or s is None:
        return "N/A"
    if r > threshold and s > threshold:
        return "Improving"
    if r < -threshold and s < -threshold:
        return "Declining"
    return "Stable"

for q in quarterly_summary:
    q["quarter_trend"] = quarter_trend(q["runs_change"], q["sr_change"])


career_bucket = defaultdict(lambda: {"runs": [], "sr": []})

for q in quarterly_summary:
    if q["runs_change"] is not None:
        career_bucket[q["player"]]["runs"].append(q["runs_change"])
        career_bucket[q["player"]]["sr"].append(q["sr_change"])

for player, vals in career_bucket.items():
    avg_runs = sum(vals["runs"]) / len(vals["runs"])
    avg_sr = sum(vals["sr"]) / len(vals["sr"])

    if avg_runs > 0.03 and avg_sr > 0.03:
        phase = "Career Ascending"
    elif avg_runs < -0.03 and avg_sr < -0.03:
        phase = "Career Declining"
    else:
        phase = "Career Stable"

    career_summary.append({
        "player": player,
        "career_phase": phase
    })

print("Quarterly Performance:")
for q in quarterly_summary:
    print(q)

print("\nCareer Summary:")
for c in career_summary:
    print(c)
